## RIPTiDe: Transcriptome-guided parsimonious flux analysis improves predictions with metabolic networks in complex environments

### Abstract

The metabolic responses of bacteria to dynamic extracellular conditions drives not only the behavior of single species, but also entire communities of microbes. Over the last decade, genome-scale metabolic network reconstructions have assisted in our appreciation of important metabolic determinants of bacterial physiology. These network models have been a powerful force in understanding the metabolic capacity that species may utilize in order to succeed in an environment. Increasingly, an understanding of context-specific metabolism is critical for elucidating metabolic drivers of larger phenotypes and disease. However, previous approaches to use these platforms in concert with omics data to better characterize experimental systems have met challenges due to assumptions necessary by the various integration platforms or due to large input data requirements. With these challenges in mind, we developed RIPTiDe (Reaction Inclusion by Parsimony and Transcript Distribution) which uses both parsimony of overall flux and transcriptomic abundances to identify the most cost-effective usage of metabolism that also best reflects the cell’s investments into transcription. Additionally, in biological samples where it is difficult to quantify specific growth conditions, it becomes critical to develop methods that require lower amounts of user intervention in order to generate accurate metabolic predictions. Utilizing a metabolic network reconstruction for the model organism Escherichia coli str. K-12 substr. MG1655, we found that RIPTiDe correctly identifies context-specific metabolic pathway activity without supervision or knowledge of specific media conditions. We also assessed the application of RIPTiDe to in vivo metatranscriptomic data where E. coli was present at high abundances, and found that our approach also predicts metabolic behaviors of host-associated bacteria with high accuracy. In the setting of human health, understanding metabolic changes within bacteria in environments where growth substrate availability is difficult to quantify can have large downstream impacts in our ability to elucidate molecular drivers of disease-associated dysbiosis across the microbiota. Toward this point, RIPTiDe has far reaching potential for understanding context-specific bacterial metabolism within complex communities.

### Testing With A Simplified Model of Bacterial Metabolism

In [1]:
from riptide import *

In [2]:
# Load in example model
toy_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/example_GENRE.sbml')

# gene1 = Glucose transporter
# gene2 = Proline transporter
# gene3 = Glycine transporter
# gene4 = Hydrogen efflux
# gene5 = Carbon dioxide efflux
# gene6 = Phosphate transporter
# gene7 = Glycolysis
# gene8 = Stickland fermentation

In [29]:
toy_model

<Model iTEST at 0x7fd2eb881750>

In [6]:
# Find most parsimonious route of flux
from cobra.flux_analysis.parsimonious import pfba
toy_solution = pfba(toy_model)
print(toy_solution.fluxes)

EX_gluc_e   -1000.0
rxn1         1000.0
EX_pro_e        0.0
rxn2            0.0
EX_gly_e        0.0
rxn3            0.0
EX_h_e       1000.0
rxn4         1000.0
EX_co2_e        0.0
rxn5            0.0
EX_pi_e     -1000.0
rxn6         1000.0
EX_adp_c    -1000.0
rxn7         1000.0
rxn8            0.0
DM_atp_c     1000.0
Name: fluxes, dtype: float64


In [3]:
from riptide import *
toy_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/example_GENRE.sbml')

# Create associated transcriptomes
peptide_transcriptome = {'gene1':1, 
                         'gene2':100, # rxn2 = Proline transporter
                         'gene3':100, # rxn3 = Glycine transporter
                         'gene4':1, 
                         'gene5':1, 
                         'gene6':1, 
                         'gene7':1, 
                         'gene8':10000} # rxn8 = Stickland fermentation

glucose_transcriptome = {'gene1':100, # rxn1 = Glucose transporter
                         'gene2':1, 
                         'gene3':1, 
                         'gene4':1, 
                         'gene5':1, 
                         'gene6':100, # rxn6 = Phosphate transporter
                         'gene7':10000, # rxn7 = Glycolysis
                         'gene8':1}

In [2]:
toy_model_peptide = riptide.contextualize(toy_model, transcriptome=peptide_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 13 from 16 (18.75% change)
Metabolites pruned to 12 from 14 (14.29% change)

RIPTiDe completed in 5 seconds



In [3]:
riptide.save_riptide_output(riptide_obj=toy_model_peptide, path='/home/mjenior/Desktop/test_peptide')

In [32]:
for cpd in toy_model_peptide.model.metabolites:
    print(cpd.id + '\t' + cpd.name)

pro_e	Proline
pro_c	Proline
gly_e	Glycine
gly_c	Glycine
h_e	H+
h_c	H+
co2_e	CO2
co2_c	CO2
pi_e	Pi
pi_c	Pi
adp_c	ADP
atp_c	ATP


In [82]:
for rxn in toy_model_peptide.model.reactions:
    print(rxn.id + '\t' + rxn.name)

EX_pro_e	Proline exchange
rxn2	Proline transport
EX_gly_e	Glycine exchange
rxn3	Glycine transport
EX_h_e	H+ exchange
rxn4	Hydrogen efflux
EX_co2_e	CO2 exchange
rxn5	Carbon dioxide efflux
EX_pi_e	Pi exchange
rxn6	Phosphate transport
EX_adp_c	ADP exchange
rxn8	Stickland fermentation
DM_atp_c	ATP demand


In [33]:
toy_model_peptide.model.slim_optimize()

1000.0

In [44]:
from itertools import chain
from copy import deepcopy

# Calculate pFBA sum of fluxes
test = deepcopy(toy_model_peptide.model)
prev_objVal = test.slim_optimize()
prev_obj_constraint = test.problem.Constraint(test.objective.expression, lb=prev_objVal*0.8, ub=prev_objVal)
test.add_cons_vars([prev_obj_constraint])
test.solver.update()
reaction_variables = ((rxn.forward_variable, rxn.reverse_variable) for rxn in test.reactions)
variables = chain(*reaction_variables)
test.objective = test.problem.Objective(symengine.RealDouble(0), direction='min', sloppy=True)
test.objective.set_linear_coefficients({v: 1.0 for v in variables})
flux_sum = test.slim_optimize()
print('pFBA sum of fluxes: ' + str(flux_sum))

# Calculate weighted pFBA sum of fluxes
test = deepcopy(toy_model_peptide.model)
prev_objVal = test.slim_optimize()
prev_obj_constraint = test.problem.Constraint(test.objective.expression, lb=prev_objVal*0.8, ub=prev_objVal)
test.add_cons_vars([prev_obj_constraint])
test.solver.update()
pfba_expr = symengine.RealDouble(0)
for rxn in test.reactions:
    try:
        pfba_expr += peptide_transcriptome[rxn.id] * rxn.forward_variable
        pfba_expr += peptide_transcriptome[rxn.id] * rxn.reverse_variable
    except:
        continue
test.objective = test.problem.Objective(pfba_expr, direction='min', sloppy=True)
test.solver.update()
flux_sum = test.slim_optimize()
print('Weighted pFBA sum of fluxes: ' + str(flux_sum))

pFBA sum of fluxes: 10400.0
Weighted pFBA sum of fluxes: 0.0


In [79]:
toy_model_glucose = riptide.contextualize(toy_model, transcriptome=glucose_transcriptome, exch_weight=True)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 9 from 16 (43.75% change)
Metabolites pruned to 8 from 14 (42.86% change)

RIPTiDe completed in 5 seconds



In [35]:
for cpd in toy_model_glucose.model.metabolites:
    print(cpd.id + '\t' + cpd.name)

gluc_e	Glucose
gluc_c	Glucose
h_e	H+
h_c	H+
pi_e	Pi
pi_c	Pi
adp_c	ADP
atp_c	ATP


In [80]:
for rxn in toy_model_glucose.model.reactions:
    print(rxn.id + '\t' + rxn.name)

EX_gluc_e	Glucose exchange
rxn1	Glucose transport
EX_h_e	H+ exchange
rxn4	Hydrogen efflux
EX_pi_e	Pi exchange
rxn6	Phosphate transport
EX_adp_c	ADP exchange
rxn7	Glycolysis
DM_atp_c	ATP demand


In [36]:
toy_model_glucose.model.slim_optimize()

1000.0

In [45]:
from itertools import chain
from copy import deepcopy

# Calculate pFBA sum of fluxes
test = deepcopy(toy_model_glucose.model)
prev_objVal = test.slim_optimize()
prev_obj_constraint = test.problem.Constraint(test.objective.expression, lb=prev_objVal*0.8, ub=prev_objVal)
test.add_cons_vars([prev_obj_constraint])
test.solver.update()
reaction_variables = ((rxn.forward_variable, rxn.reverse_variable) for rxn in test.reactions)
variables = chain(*reaction_variables)
test.objective = test.problem.Objective(symengine.RealDouble(0), direction='min', sloppy=True)
test.objective.set_linear_coefficients({v: 1.0 for v in variables})
flux_sum = test.slim_optimize()
print('pFBA sum of fluxes: ' + str(flux_sum))

# Calculate weighted pFBA sum of fluxes
test = deepcopy(toy_model_glucose.model)
prev_objVal = test.slim_optimize()
prev_obj_constraint = test.problem.Constraint(test.objective.expression, lb=prev_objVal*0.8, ub=prev_objVal)
test.add_cons_vars([prev_obj_constraint])
test.solver.update()
pfba_expr = symengine.RealDouble(0)
for rxn in test.reactions:
    try:
        pfba_expr += glucose_transcriptome[rxn.id] * rxn.forward_variable
        pfba_expr += glucose_transcriptome[rxn.id] * rxn.reverse_variable
    except:
        continue
test.objective = test.problem.Objective(pfba_expr, direction='min', sloppy=True)
test.solver.update()
flux_sum = test.slim_optimize()
print('Weighted pFBA sum of fluxes: ' + str(flux_sum))

pFBA sum of fluxes: 7200.0
Weighted pFBA sum of fluxes: 0.0


In [5]:
# Test with CORDA as well

# Define thresholds
corda_lo_threshold, corda_hi_threshold = numpy.percentile(list(peptide_transcriptome.values()), [50 ,75])

# Format data for CORDA
corda_gene_confidences = {}
for gene in peptide_transcriptome.keys():
    if peptide_transcriptome[gene] < corda_lo_threshold: confidence = 0
    elif peptide_transcriptome[gene] >= corda_lo_threshold and peptide_transcriptome[gene] < corda_hi_threshold: confidence = 1
    elif peptide_transcriptome[gene] >= corda_hi_threshold: confidence = 3
    else: confidence = -1
    corda_gene_confidences[gene] = confidence

corda_peptide_confidences = {}
corda_peptide_confidences['DM_atp_c'] = 3
for gene in toy_model.genes:
    try:
        confidence = corda_gene_confidences[gene.id]
    except:
        continue
    reactions = [x.id for x in list(gene.reactions)]
    for rxn in reactions:
        corda_peptide_confidences[rxn] = confidence
        
for rxn in toy_model.reactions:
    if rxn.id not in corda_peptide_confidences.keys():
        corda_peptide_confidences[rxn.id] = 0


In [75]:
# Run CORDA
from corda import CORDA

# Run CORDA       
optimal = CORDA(toy_model, corda_rxn_confidences)
optimal.build()
CORDA = []
for rxn in optimal.included.keys():
    if optimal.included[rxn] == True:
        CORDA.append(rxn)
        
# Create new model
toy_model_corda = copy.deepcopy(toy_model)
for rxn in toy_model_corda.reactions:
    if not rxn.id in CORDA:
        toy_model_corda.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)

In [76]:
toy_model_corda.slim_optimize()

1000.0

In [77]:
# Nothing pruned
for cpd in toy_model_corda.metabolites:
    print(cpd.id + '\t' + cpd.name)

gluc_e	Glucose
gluc_c	Glucose
pro_e	Proline
pro_c	Proline
gly_e	Glycine
gly_c	Glycine
h_e	H+
h_c	H+
co2_e	CO2
co2_c	CO2
pi_e	Pi
pi_c	Pi
adp_c	ADP
atp_c	ATP


In [83]:
for rxn in toy_model_corda.reactions:
    print(rxn.id + '\t' + rxn.name)

rxn1	Glucose transport
EX_pro_e	Proline exchange
rxn2	Proline transport
EX_gly_e	Glycine exchange
rxn3	Glycine transport
EX_h_e	H+ exchange
rxn4	Hydrogen efflux
EX_co2_e	CO2 exchange
rxn5	Carbon dioxide efflux
EX_pi_e	Pi exchange
rxn6	Phosphate transport
EX_adp_c	ADP exchange
rxn8	Stickland fermentation
DM_atp_c	ATP demand


In [49]:
# RegrEx
regrex = ['rxn2','rxn3','EX_h_e','rxn4','EX_co2_e','rxn5','rxn6','rxn8','DM_atp_c','EX_pro_e','EX_gly_e','EX_pi_e','EX_adp_c']

toy_model_regrex = copy.deepcopy(toy_model)
for rxn in toy_model_regrex.reactions:
    if not rxn.id in regrex:
        toy_model_regrex.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)

In [48]:
toy_model_regrex.slim_optimize()

1000.0

In [50]:
for cpd in toy_model_regrex.metabolites:
    print(cpd.id + '\t' + cpd.name)

gluc_e	Glucose
gluc_c	Glucose
pro_e	Proline
pro_c	Proline
gly_e	Glycine
gly_c	Glycine
h_e	H+
h_c	H+
co2_e	CO2
co2_c	CO2
pi_e	Pi
pi_c	Pi
adp_c	ADP
atp_c	ATP


In [60]:
for rxn in toy_model_regrex.reactions:
    print(rxn.id + '\t' + rxn.name)

rxn1	Glucose transport
EX_pro_e	Proline exchange
rxn2	Proline transport
EX_gly_e	Glycine exchange
rxn3	Glycine transport
EX_h_e	H+ exchange
rxn4	Hydrogen efflux
EX_co2_e	CO2 exchange
rxn5	Carbon dioxide efflux
EX_pi_e	Pi exchange
rxn6	Phosphate transport
EX_adp_c	ADP exchange
rxn8	Stickland fermentation
DM_atp_c	ATP demand


### Testing with E.coli K-12 MG1655 model

In [4]:
iJO1366 = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366.xml')
iJO1366.objective = iJO1366.reactions.BIOMASS_Ec_iJO1366_WT_53p95M

# Open all exchanges
exchanges = set()
for rxn in iJO1366.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (min(rxn.lower_bound, -1000.), max(rxn.upper_bound, 1000.))
        exchanges |= set([rxn.id])

In [4]:
iJO1366

<Model iJO1366 at 0x7f22a74f12d0>

In [5]:
len(iJO1366.genes)

1367

In [3]:
def max_doubling_time(model):
    
    with model as m: 
        growth =  m.slim_optimize()
    
    if growth < 1e-6:
        growth = 'No growth'
    else:    
        growth = (1.0 / growth) * 3600.0
        if growth < 60.0:
            growth = str(round(growth, 1)) + ' minutes'
        else:
            growth = growth / 60.0
            growth = str(round(growth, 3)) + ' hours'
            
    print(growth)


def collect_doubling_times(flux_samples, biomass):
    biomass = list(flux_samples[biomass])
    times = []
    
    for x in biomass:
        growth = (1.0 / x) * 3600.0 # Calculated in minutes
        growth = round(growth, 2)
        times.append(growth)
        
    return times


def collect_growth_rates(flux_samples, biomass):
    biomass = list(flux_samples[biomass])
    rates = []
    
    for x in biomass:
        rate = x / 60.0
        rate = round(rate, 3)
        rates.append(rate)
        
    return rates

In [7]:
max_doubling_time(iJO1366)

34.0 minutes


### Contextualizing Published Datasets

In [3]:
# Read in transcriptomes

# Data collected from:
# Monk et al. (2016). Multi-omics Quantification of Species Variation of Escherichia coli
# Links Molecular Features with Strain Phenotypes. Cell Systems. 3; 238–251.

# Load in GPR translations
gpr_dict = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/iJO1366_genes.tsv', 'r') as genes:
    for line in genes:
        line = line.split()
        gpr_dict[line[1]] = line[0]

# Normalized abundances
# Separate into treatment goups and calculate medians
m9_aerobic = {}
m9_anaerobic = {}     
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/normalized.tsv', 'r') as transcription:
    for line in transcription:
        line = line.split()
        if line[0] == 'gene':
            continue
        else:
            try:
                gene = gpr_dict[line[0]]
            except:
                continue
            m9_aerobic[gene] = numpy.median([int(x) for x in line[1:4]])
            m9_anaerobic[gene] = numpy.median([int(y) for y in line[4:7]])
            
# Rich media (LB) data from:
# Double-stranded transcriptome of E. coli
# Meghan Lybecker, Bob Zimmermann, Ivana Bilusic, Nadezda Tukhtubaeva, Renée Schroeder
# Proceedings of the National Academy of Sciences Feb 2014, 111 (8) 3134-3139; DOI: 10.1073/pnas.1315974111
lb_aerobic = {}     
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Lybecker_2014.mapped.norm.tsv', 'r') as transcription:
    header = transcription.readline()
    for line in transcription: 
        line = line.split()
        lb_aerobic[line[0]] = float(line[1])

In [12]:
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/lb_aerobic.driven_formatted.csv', 'w') as outfile:
    for gene in lb_aerobic.keys():
        entry = gene + ',' + str(lb_aerobic[gene]) + '\n'
        outfile.write(entry)

### Sensitivity testing for minimum objective flux

In [7]:
iJO1366_10 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.1)
iJO1366_20 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.2)
iJO1366_30 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.3)
iJO1366_40 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.4)
iJO1366_50 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.5)
iJO1366_60 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.6)
iJO1366_70 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.7)
iJO1366_80 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.8)
iJO1366_90 = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, fraction = 0.9)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 445 from 2583 (82.77% change)
Metabolites pruned to 451 from 1805 (75.01% change)
Flux through the objective DECREASED to ~20.38 from ~105.77 (80.73% change)
Contextualized metabolism has a concordancy of 39.0% (p<0.001) with the transcriptome

RIPTiDe completed in 37 seconds


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 446 from 2583 (82.73% change)
Metabolites pruned to 451 from 1805 (75.01% change)
Flux through the objective DECREASED to ~21.99 from ~105.77 (79.21% change)
Contextualized metabolism has a concordancy of 38.6% (p<0.001) with the transcriptome

RIPTiDe completed in 36 seconds


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific f

ValueError: Cannot take a larger sample than population when 'replace=False'

### Comparing to exchanged-constrained pFBA

In [4]:
# Set media 

m9_aer_components = ['EX_o2_e', 
                 'EX_glc__D_e', 
                 'EX_mg2_e', 
                 'EX_so4_e', 
                 'EX_ca2_e', 
                 'EX_cl_e', 
                 'EX_ca2_e', 
                 'EX_h2o_e', 
                 'EX_na1_e', 
                 'EX_k_e', 
                 'EX_h_e', 
                 'EX_pi_e', 
                 'EX_nh4_e',
                 
                 # Trace co-factors (essential)
                 'EX_adocbl_e',
                 'EX_cobalt2_e',
                 'EX_cu2_e',
                 'EX_fe3dcit_e',
                 'EX_mn2_e',
                 'EX_mobd_e',
                 'EX_ni2_e',
                 'EX_zn2_e']

m9_anaer_components = ['EX_glc__D_e', 
                 'EX_mg2_e', 
                 'EX_so4_e', 
                 'EX_ca2_e', 
                 'EX_cl_e', 
                 'EX_ca2_e', 
                 'EX_h2o_e', 
                 'EX_na1_e', 
                 'EX_k_e', 
                 'EX_h_e', 
                 'EX_pi_e', 
                 'EX_nh4_e',
                 
                 # Trace co-factors (essential)
                 'EX_adocbl_e',
                 'EX_cobalt2_e',
                 'EX_cu2_e',
                 'EX_fe3dcit_e',
                 'EX_mn2_e',
                 'EX_mobd_e',
                 'EX_ni2_e',
                 'EX_zn2_e']

lb_aer_components = ['EX_ala_e',
                     'EX_arg_e',
                     'EX_asp_e',
                     'EX_cys_e',
                     'EX_glu_e',
                     'EX_gly_e',
                     'EX_his_e',
                     'EX_ile_e',
                     'EX_leu_e',
                     'EX_lys_e',
                     'EX_met_e',
                     'EX_pro_e',
                     'EX_thr_e',
                     'EX_tyr_e',
                     'EX_phe_e',
                     'EX_ser_e',
                     'EX_trp_e',
                     'EX_val_e',
                     'EX_pnto_e',
                     'EX_nac_e',
                     'EX_na1_e',
                     'EX_cl_e',
                     'EX_so4_e',
                     'EX_k_e',
                     'EX_pi_e',
                     'EX_ca2_e',
                     'EX_mg2_e',
                     'EX_zn2_e',
                     'EX_aso3_e',
                     'EX_cd2_e',
                     'EX_hg2_e',
                     'EX_h_e',
                     'EX_h2o_e',
                     'EX_o2_e',
                     'EX_ins_e',
                     'EX_hxan_e',
                     'EX_dcyt_e',
                     'EX_thymd_e',
                     'EX_ura_e',
                     'EX_uri_e',
                     'EX_dad_e',
                     'EX_adn_e',
                     'EX_co2_e',
                     'EX_cobalt2_e',
                     'EX_cu2_e',
                     'EX_fe2_e',
                     'EX_fe3_e',
                     'EX_mn2_e',
                     'EX_mobd_e',
                     'EX_tungs_e',
                     'EX_cbl1_e',
                     'EX_fru_e',
                     'EX_gal_e',
                     'EX_ni2_e',
                     'EX_sel_e',
                     'EX_slnt_e',
                # Trace co-factors (essential)
                 'EX_adocbl_e',
                 'EX_cobalt2_e',
                 'EX_cu2_e',
                 'EX_fe3dcit_e',
                 'EX_mn2_e',
                 'EX_mobd_e',
                 'EX_ni2_e',
                 'EX_zn2_e']
m9_aer_components = list(set(m9_aer_components))
m9_anaer_components = list(set(m9_anaer_components))
lb_aer_components = list(set(lb_aer_components))

# Create copies
iJO1366_m9_aer = copy.deepcopy(iJO1366)
iJO1366_m9_anaer = copy.deepcopy(iJO1366)
iJO1366_lb_aer = copy.deepcopy(iJO1366)

# Close non-defined exchanges and collect reactants
m9_substrates = []
for rxn in exchanges:
    if not rxn in m9_aer_components:
        iJO1366_m9_aer.reactions.get_by_id(rxn).bounds = (0., max(iJO1366_m9_aer.reactions.get_by_id(rxn).upper_bound, 1000.))
        
    if not rxn in m9_anaer_components:
        iJO1366_m9_anaer.reactions.get_by_id(rxn).bounds = (0., max(iJO1366_m9_anaer.reactions.get_by_id(rxn).upper_bound, 1000.))

    if not rxn in lb_aer_components:
        iJO1366_lb_aer.reactions.get_by_id(rxn).bounds = (0., max(iJO1366_lb_aer.reactions.get_by_id(rxn).upper_bound, 1000.))


In [8]:
# Constrain objective flux

# Base model
iJO1366_max = copy.deepcopy(iJO1366)
prev_obj_val = iJO1366_max.slim_optimize()
prev_obj_constraint = iJO1366_max.problem.Constraint(iJO1366_max.objective.expression, lb=prev_obj_val*0.8, ub=prev_obj_val)
iJO1366_max.add_cons_vars([prev_obj_constraint])
iJO1366_max.solver.update()

# M9 + O2 constraints
iJO1366_m9_aer_max = copy.deepcopy(iJO1366_m9_aer)
prev_obj_val = iJO1366_m9_aer_max.slim_optimize()
prev_obj_constraint = iJO1366_m9_aer_max.problem.Constraint(iJO1366_m9_aer_max.objective.expression, lb=prev_obj_val*0.8, ub=prev_obj_val)
iJO1366_m9_aer_max.add_cons_vars([prev_obj_constraint])
iJO1366_m9_aer_max.solver.update()

# M9 - O2 constraints
iJO1366_m9_anaer_max = copy.deepcopy(iJO1366_m9_anaer)
prev_obj_val = iJO1366_m9_anaer_max.slim_optimize()
prev_obj_constraint = iJO1366_m9_anaer_max.problem.Constraint(iJO1366_m9_anaer_max.objective.expression, lb=prev_obj_val*0.8, ub=prev_obj_val)
iJO1366_m9_anaer_max.add_cons_vars([prev_obj_constraint])
iJO1366_m9_anaer_max.solver.update()

# LB + O2 constraints
iJO1366_lb_aer_max = copy.deepcopy(iJO1366_lb_aer)
prev_obj_val = iJO1366_lb_aer_max.slim_optimize()
prev_obj_constraint = iJO1366_lb_aer_max.problem.Constraint(iJO1366_lb_aer_max.objective.expression, lb=prev_obj_val*0.8, ub=prev_obj_val)
iJO1366_lb_aer_max.add_cons_vars([prev_obj_constraint])
iJO1366_lb_aer_max.solver.update()

In [6]:
# gapsplit flux sampler
# Keaty TC & Jensen PA (2019). gapsplit: Efficient random sampling for non-convex constraint-based models.
# bioRxiv 652917; doi: https://doi.org/10.1101/652917 

def gapsplit(model, n=500):

    # Define a few more variables
    max_tries=1000
    primary_tol=0.001
    secondary_frac=0.05
    min_range=1e-5
    enforce_range=True

    reactions = model.reactions
    fva = flux_variability_analysis(model, reactions, fraction_of_optimum=0.001)

    if secondary_frac >= 1.0:
        n_secondary = secondary_frac
    else:
        n_secondary = numpy.floor(secondary_frac * len(model.reactions)).astype(int)

    idxs = (fva.maximum - fva.minimum >= min_range).to_numpy().nonzero()[0]
    weights = (1.0 / (fva.maximum - fva.minimum) ** 2).to_numpy()

    samples = numpy.zeros((n, len(model.reactions)))
    k = 0
    infeasible_count = 0

    for try_ in range(max_tries):
        relative, target, width = maxgap(samples[0:k,idxs], fva.iloc[idxs,:])
        
        primary_var = numpy.argmax(relative)
        primary_target = target[primary_var]
        primary_lb = primary_target - primary_tol*width[primary_var]
        primary_ub = primary_target + primary_tol*width[primary_var]

        secondary_vars = numpy.random.choice(len(idxs), n_secondary, replace=False)
        secondary_targets = target[secondary_vars]
        secondary_weights = weights[idxs[secondary_vars]]

        new_sample = generate_sample(
            model, idxs[primary_var], primary_lb, primary_ub,
            idxs[secondary_vars], secondary_targets, secondary_weights)
        if new_sample is not None:
            if enforce_range:
                new_sample[new_sample > fva.maximum] = fva.maximum[new_sample > fva.maximum]
                new_sample[new_sample < fva.minimum] = fva.minimum[new_sample < fva.minimum]

            samples[k,:] = new_sample
            k += 1
        else:
            infeasible_count += 1

        if k >= n: break

    if k < n:
        samples = samples[:k,:]
    return pandas.DataFrame(data=samples,columns=fva.maximum.index)


def generate_sample(
        model, primary_var, primary_lb, primary_ub,
        secondary_vars=None, secondary_targets=None, secondary_weights=None):
    with model:
        model.reactions[primary_var].lower_bound = primary_lb
        model.reactions[primary_var].upper_bound = primary_ub
        model.objective = symengine.RealDouble(0)
        solution = model.optimize()
        if solution.status != 'optimal':
            return None
        else:
            return solution.fluxes


def maxgap(points, fva):
    points = points.copy()
    points = numpy.vstack((fva.minimum, points, fva.maximum))
    points.sort(0)

    gaps = points[1:,:] - points[0:-1,:]
    width = gaps.max(0)
    loc = gaps.argmax(0)
    left = numpy.zeros(width.size)
    for i in range(width.size):
        left[i] = points[loc[i],i]

    relative = width / (points[-1,:] - points[0,:])
    target = left + width / 2.0
    
    
    return relative, target, width


In [9]:
# Flux sample unconstrained base model
raw_fluxsamples = gapsplit(iJO1366)

In [10]:
# Flux sample objective flux constrained
max_fluxsamples = gapsplit(iJO1366_max)

In [11]:
# Flux sample media constrained base models
raw_m9_aer_fluxsamples = gapsplit(iJO1366_m9_aer)
raw_m9_anaer_fluxsamples = gapsplit(iJO1366_m9_anaer)
raw_lb_aer_fluxsamples = gapsplit(iJO1366_lb_aer)

In [12]:
# Flux sample objective flux constrained, media constrained models
max_m9_aer_fluxsamples = gapsplit(iJO1366_m9_aer_max)
max_m9_anaer_fluxsamples = gapsplit(iJO1366_m9_anaer_max)
max_lb_aer_fluxsamples = gapsplit(iJO1366_lb_aer_max)

In [7]:
# Get RIPTiDe flux samples without exchange constraints
iJO1366_m9_aer_riptide = riptide.contextualize(iJO1366, transcriptome=m9_aerobic)
riptide_m9_aer_fluxsamples = iJO1366_m9_aer_riptide.flux_samples


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 478 from 2583 (81.49% change)
Metabolites pruned to 475 from 1805 (73.68% change)
Flux through the objective DECREASED to ~84.74 from ~105.77 (19.88% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 2 minutes and 45 seconds



In [19]:
cobra.io.save_matlab_model(iJO1366_m9_aer_riptide.model, '/home/mjenior/Desktop/iJO1366_m9.mat')
iJO1366_m9_aer_riptide.flux_samples[:1].to_csv('/home/mjenior/Desktop/iJO1366_m9.flux_distribution.tsv', sep='\t', index=None, header=True)

In [15]:
# Subset to just exchange levels and write to files
exchanges = set([y.id for y in iJO1366_m9_aer_riptide.model.reactions if 'EX_' in y.id])

temp1 = raw_fluxsamples.loc[0:, exchanges]
temp2 = max_fluxsamples.loc[0:, exchanges]
raw_m9_aer_fluxsamples = raw_m9_aer_fluxsamples.loc[0:, exchanges]
max_m9_aer_fluxsamples = max_m9_aer_fluxsamples.loc[0:, exchanges]
riptide_m9_aer_fluxsamples = riptide_m9_aer_fluxsamples.loc[0:, exchanges]

temp1.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_aerobic/raw.iJO1366.exchange_fluxes.tsv', sep='\t')
temp2.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_aerobic/max.iJO1366.exchange_fluxes.tsv', sep='\t')
raw_m9_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_aerobic/raw_m9a.iJO1366.exchange_fluxes.tsv', sep='\t')
max_m9_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_aerobic/max_m9a.iJO1366.exchange_fluxes.tsv', sep='\t')
riptide_m9_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_aerobic/riptide.m9a.iJO1366.exchange_fluxes.tsv', sep='\t')

In [16]:
# Get RIPTiDe flux samples without exchange constraints
iJO1366_m9_anaer_riptide = riptide.contextualize(iJO1366, transcriptome=m9_anaerobic)
riptide_m9_anaer_fluxsamples = iJO1366_m9_anaer_riptide.flux_samples


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 474 from 2583 (81.65% change)
Metabolites pruned to 472 from 1805 (73.85% change)
Flux through the objective DECREASED to ~85.64 from ~105.77 (19.03% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 1 minutes and 27 seconds



In [19]:
# Subset to just exchange levels and write to files
exchanges = set([y.id for y in iJO1366_m9_anaer_riptide.model.reactions if 'EX_' in y.id])

temp1 = raw_fluxsamples.loc[0:, exchanges]
temp2 = max_fluxsamples.loc[0:, exchanges]
raw_m9_anaer_fluxsamples = raw_m9_anaer_fluxsamples.loc[0:, exchanges]
max_m9_anaer_fluxsamples = max_m9_anaer_fluxsamples.loc[0:, exchanges]
riptide_m9_anaer_fluxsamples = riptide_m9_anaer_fluxsamples.loc[0:, exchanges]

temp1.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_anaerobic/raw.iJO1366.exchange_fluxes.tsv', sep='\t')
temp2.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_anaerobic/max.iJO1366.exchange_fluxes.tsv', sep='\t')
raw_m9_anaer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_anaerobic/raw_m9n.iJO1366.exchange_fluxes.tsv', sep='\t')
max_m9_anaer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_anaerobic/max_m9n.iJO1366.exchange_fluxes.tsv', sep='\t')
riptide_m9_anaer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/m9_anaerobic/riptide.m9n.iJO1366.exchange_fluxes.tsv', sep='\t')

In [20]:
# Get RIPTiDe flux samples without exchange constraints
iJO1366_lb_aer_riptide = riptide.contextualize(iJO1366, transcriptome=lb_aerobic)
riptide_lb_aer_fluxsamples = iJO1366_lb_aer_riptide.flux_samples


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 453 from 2583 (82.46% change)
Metabolites pruned to 454 from 1805 (74.85% change)
Flux through the objective DECREASED to ~85.67 from ~105.77 (19.0% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 1 minutes and 28 seconds



In [21]:
# Subset to just exchange levels and write to files
exchanges = set([y.id for y in iJO1366_lb_aer_riptide.model.reactions if 'EX_' in y.id])

temp1 = raw_fluxsamples.loc[0:, exchanges]
temp2 = max_fluxsamples.loc[0:, exchanges]
raw_lb_aer_fluxsamples = raw_lb_aer_fluxsamples.loc[0:, exchanges]
max_lb_aer_fluxsamples = max_lb_aer_fluxsamples.loc[0:, exchanges]
riptide_lb_aer_fluxsamples = riptide_lb_aer_fluxsamples.loc[0:, exchanges]

temp1.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/lb_aerobic/raw.iJO1366.exchange_fluxes.tsv', sep='\t')
temp2.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/lb_aerobic/max.iJO1366.exchange_fluxes.tsv', sep='\t')
raw_lb_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/lb_aerobic/raw_lb.iJO1366.exchange_fluxes.tsv', sep='\t')
max_lb_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/lb_aerobic/max_lb.iJO1366.exchange_fluxes.tsv', sep='\t')
riptide_lb_aer_fluxsamples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/exchanges/lb_aerobic/riptide.lb.iJO1366.exchange_fluxes.tsv', sep='\t')

### Comparing across conditions

In [23]:
# Aerobic growth in M9 + glucose
iJO1366_m9_aerobic = riptide.contextualize(iJO1366, transcriptome=m9_aerobic)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 478 from 2583 (81.49% change)
Metabolites pruned to 475 from 1805 (73.68% change)
Flux through the objective DECREASED to ~84.74 from ~105.77 (19.88% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 3 minutes and 16 seconds



In [11]:
print('Genes: ' + str(len(iJO1366_m9_aerobic.model.genes)))

Genes: 383


In [5]:
# Anaerobic growth in M9 + glucose
#iJO1366.reactions.get_by_id('EX_o2_e').lower_bound = 0.0 # make anaerobic
iJO1366_m9_anaerobic = riptide.contextualize(iJO1366, transcriptome=m9_anaerobic)
#iJO1366.reactions.get_by_id('EX_o2_e').lower_bound = -1000.0 # revert change


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 475 from 2583 (81.61% change)
Metabolites pruned to 473 from 1805 (73.8% change)
Flux through the objective DECREASED to ~85.64 from ~105.77 (19.03% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 2 minutes and 8 seconds



In [9]:
print('Genes: ' + str(len(iJO1366_m9_anaerobic.model.genes)))

Genes: 408


In [4]:
# Aerobic growth in LB
iJO1366_lb_aerobic = riptide.contextualize(iJO1366, transcriptome=lb_aerobic)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 457 from 2583 (82.31% change)
Metabolites pruned to 459 from 1805 (74.57% change)
Flux through the objective DECREASED to ~87.02 from ~105.77 (17.73% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 2 minutes and 35 seconds



In [10]:
print('Genes: ' + str(len(iJO1366_lb_aerobic.model.genes)))

Genes: 395


In [5]:
# Compare to base implementation of pFBA
# All coefficients set to 1.0
pfba_transcriptome = {}
for gene in lb_aerobic.keys(): pfba_transcriptome[gene] = 1.0
iJO1366_pfba = riptide.contextualize(iJO1366, transcriptome=pfba_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 454 from 2583 (82.42% change)
Metabolites pruned to 454 from 1805 (74.85% change)
Flux through the objective DECREASED to ~86.89 from ~105.77 (17.85% change)

RIPTiDe completed in 2 minutes and 26 seconds



In [11]:
print('Genes: ' + str(len(iJO1366_pfba.model.genes)))

Genes: 377


In [12]:
# Save contextualized reconstructions
cobra.io.save_json_model(iJO1366_m9_aerobic.model, '/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366_m9_aerobic.json')
cobra.io.save_json_model(textbook_model, "test.json")cobra.io.save_json_model(iJO1366_m9_anaerobic.model, '/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366_m9_anaerobic.json')
cobra.io.save_json_model(iJO1366_lb_aerobic.model, '/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366_lb_aerobic.json')
cobra.io.save_json_model(iJO1366_pfba.model, '/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366_pfba.json')

In [20]:
# Collect growth rates
base_rate = iJO1366.slim_optimize()
base_rate = (1.0 / base_rate) * 3600.0
base_rate = round(base_rate, 2)
print('Unconstrained: ' + str(base_rate) + ' minutes')

m9_aerobic_rate = iJO1366_m9_aerobic.model.slim_optimize()
m9_aerobic_rate = (1.0 / m9_aerobic_rate) * 3600.0
m9_aerobic_rate = round(base_rate, 2)
print('M9 aerobic: ' + str(m9_aerobic_rate) + ' minutes')

m9_anaerobic_rate = iJO1366_m9_anaerobic.model.slim_optimize()
m9_anaerobic_rate = (1.0 / m9_anaerobic_rate) * 3600.0
m9_anaerobic_rate = round(m9_anaerobic_rate, 2)
print('M9 anaerobic: ' + str(m9_anaerobic_rate) + ' minutes')

lb_aerobic_rate = iJO1366_lb_aerobic.model.slim_optimize()
lb_aerobic_rate = (1.0 / pfba_rate) * 3600.0
lb_aerobic_rate = round(lb_aerobic_rate, 2)
print('LB: ' + str(lb_aerobic_rate) + ' minutes')

pfba_rate = iJO1366_pfba.model.slim_optimize()
pfba_rate = (1.0 / pfba_rate) * 3600.0
pfba_rate = round(pfba_rate, 2)
print('pFBA: ' + str(pfba_rate) + ' minutes')

Unconstrained: 34.04 minutes
M9 aerobic: 34.04 minutes


NameError: name 'iJO1366_m9_anaerobic' is not defined

In [17]:
# Compares lists to create diagrams for 4 groups
def venn_comparison(list1, list2, list3, list4):
        
    # Confirm correct data types
    list1 = set(list1)
    list2 = set(list2)
    list3 = set(list3)
    list4 = set(list4)
    
    # Identify exclusive elements
    list1_only = list1.difference(list2)
    list1_only = list1_only.difference(list3)
    list1_only = list1_only.difference(list4)
    list2_only = list2.difference(list1)
    list2_only = list2_only.difference(list3)
    list2_only = list2_only.difference(list4)
    list3_only = list3.difference(list1)
    list3_only = list3_only.difference(list2)
    list3_only = list3_only.difference(list4)
    list4_only = list4.difference(list1)
    list4_only = list4_only.difference(list2)
    list4_only = list4_only.difference(list3)

    # Find overlap between just 2 groups
    list1_list2_overlap = list1.intersection(list2)
    list1_list2_overlap = list1_list2_overlap.difference(list3)
    list1_list2_overlap = list1_list2_overlap.difference(list4)
    list1_list3_overlap = list1.intersection(list3)
    list1_list3_overlap = list1_list3_overlap.difference(list2)
    list1_list3_overlap = list1_list3_overlap.difference(list4)
    list1_list4_overlap = list1.intersection(list4)
    list1_list4_overlap = list1_list4_overlap.difference(list2)
    list1_list4_overlap = list1_list4_overlap.difference(list3)
    list2_list3_overlap = list2.intersection(list3)
    list2_list3_overlap = list2_list3_overlap.difference(list1)
    list2_list3_overlap = list2_list3_overlap.difference(list4)
    list2_list4_overlap = list2.intersection(list4)
    list2_list4_overlap = list2_list4_overlap.difference(list1)
    list2_list4_overlap = list2_list4_overlap.difference(list3)
    list3_list4_overlap = list3.intersection(list4)
    list3_list4_overlap = list3_list4_overlap.difference(list1)
    list3_list4_overlap = list3_list4_overlap.difference(list2)

    # Find overlap in 3 groups
    list1_list2_list3_overlap = list1.intersection(list2)
    list1_list2_list3_overlap = list1_list2_list3_overlap.intersection(list3)
    list1_list2_list3_overlap = list1_list2_list3_overlap.difference(list4)
    list1_list2_list4_overlap = list1.intersection(list2)
    list1_list2_list4_overlap = list1_list2_list4_overlap.intersection(list4)
    list1_list2_list4_overlap = list1_list2_list4_overlap.difference(list3)
    list1_list3_list4_overlap = list1.intersection(list3)
    list1_list3_list4_overlap = list1_list3_list4_overlap.intersection(list4)
    list1_list3_list4_overlap = list1_list3_list4_overlap.difference(list2)
    list2_list3_list4_overlap = list2.intersection(list3)
    list2_list3_list4_overlap = list2_list3_list4_overlap.intersection(list4)
    list2_list3_list4_overlap = list2_list3_list4_overlap.difference(list1)
    
    # Find overlap between all groups
    all_list_overlap = list1.intersection(list2)
    all_list_overlap = all_list_overlap.intersection(list3)
    all_list_overlap = all_list_overlap.intersection(list4)
    
    # Calculate totals in each group
    list1_total = float(len(list1))
    list2_total = float(len(list2))
    list3_total = float(len(list3))
    list4_total = float(len(list4))
    list1_only_total = float(len(list1_only))
    list2_only_total = float(len(list2_only))
    list3_only_total = float(len(list3_only))
    list4_only_total = float(len(list4_only))
    list1_list2_overlap_total = float(len(list1_list2_overlap))
    list1_list3_overlap_total = float(len(list1_list3_overlap))
    list1_list4_overlap_total = float(len(list1_list4_overlap))
    list2_list3_overlap_total = float(len(list2_list3_overlap))
    list2_list4_overlap_total = float(len(list2_list4_overlap))
    list3_list4_overlap_total = float(len(list3_list4_overlap))
    list1_list2_list3_overlap_total = float(len(list1_list2_list3_overlap))
    list1_list2_list4_overlap_total = float(len(list1_list2_list4_overlap))
    list1_list3_list4_overlap_total = float(len(list1_list3_list4_overlap))
    list2_list3_list4_overlap_total = float(len(list2_list3_list4_overlap))
    all_list_overlap_total = float(len(all_list_overlap))
    
    # Calculate percent overlaps
    list1_only_percent = round(((list1_only_total / list1_total) * 100.0), 1)
    list2_only_percent = round(((list2_only_total / list2_total) * 100.0), 1)
    list3_only_percent = round(((list3_only_total / list3_total) * 100.0), 1)
    list4_only_percent = round(((list4_only_total / list4_total) * 100.0), 1)
    temp1 = (list1_list2_overlap_total / list1_total) * 100.0
    temp2 = (list1_list2_overlap_total / list2_total) * 100.0
    list1_list2_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list1_list3_overlap_total / list1_total) * 100.0
    temp2 = (list1_list3_overlap_total / list3_total) * 100.0
    list1_list3_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list1_list4_overlap_total / list1_total) * 100.0
    temp2 = (list1_list4_overlap_total / list4_total) * 100.0
    list1_list4_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list2_list3_overlap_total / list2_total) * 100.0
    temp2 = (list2_list3_overlap_total / list3_total) * 100.0
    list2_list3_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list2_list4_overlap_total / list2_total) * 100.0
    temp2 = (list2_list4_overlap_total / list4_total) * 100.0
    list2_list4_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list3_list4_overlap_total / list3_total) * 100.0
    temp2 = (list3_list4_overlap_total / list4_total) * 100.0
    list3_list4_overlap_percent = round(numpy.mean([temp1, temp2]), 1)
    temp1 = (list1_list2_list3_overlap_total / list1_total) * 100.0
    temp2 = (list1_list2_list3_overlap_total / list2_total) * 100.0
    temp3 = (list1_list2_list3_overlap_total / list3_total) * 100.0
    list1_list2_list3_overlap_percent = round(numpy.mean([temp1, temp2, temp3]), 1)
    temp1 = (list1_list2_list4_overlap_total / list1_total) * 100.0
    temp2 = (list1_list2_list4_overlap_total / list2_total) * 100.0
    temp3 = (list1_list2_list4_overlap_total / list4_total) * 100.0
    list1_list2_list4_overlap_percent = round(numpy.mean([temp1, temp2, temp3]), 1)
    temp1 = (list1_list3_list4_overlap_total / list1_total) * 100.0
    temp2 = (list1_list3_list4_overlap_total / list3_total) * 100.0
    temp3 = (list1_list3_list4_overlap_total / list4_total) * 100.0
    list1_list3_list4_overlap_percent = round(numpy.mean([temp1, temp2, temp3]), 1)
    temp1 = (list2_list3_list4_overlap_total / list2_total) * 100.0
    temp2 = (list2_list3_list4_overlap_total / list3_total) * 100.0
    temp3 = (list2_list3_list4_overlap_total / list4_total) * 100.0
    list2_list3_list4_overlap_percent = round(numpy.mean([temp1, temp2, temp3]), 1)
    temp1 = (all_list_overlap_total / list1_total) * 100.0
    temp2 = (all_list_overlap_total / list2_total) * 100.0
    temp3 = (all_list_overlap_total / list3_total) * 100.0
    temp4 = (all_list_overlap_total / list4_total) * 100.0
    all_list_overlap_percent = round(numpy.mean([temp1, temp2, temp3, temp4]), 1)
    
    # Print report to the screen
    print('List 1 only: ' + str(list1_only_percent) + '% (' + str(int(list1_only_total)) + ')')
    print('List 2 only: ' + str(list2_only_percent) + '% (' + str(int(list2_only_total)) + ')')
    print('List 3 only: ' + str(list3_only_percent) + '% (' + str(int(list3_only_total)) + ')')
    print('List 4 only: ' + str(list4_only_percent) + '% (' + str(int(list4_only_total)) + ')')
    print('')
    print('List 1 + List 2: ' + str(list1_list2_overlap_percent) + '% (' + str(int(list1_list2_overlap_total)) + ')')
    print('List 1 + List 3: ' + str(list1_list3_overlap_percent) + '% (' + str(int(list1_list3_overlap_total)) + ')')
    print('List 1 + List 4: ' + str(list1_list4_overlap_percent) + '% (' + str(int(list1_list4_overlap_total)) + ')')
    print('List 2 + List 3: ' + str(list2_list3_overlap_percent) + '% (' + str(int(list2_list3_overlap_total)) + ')')
    print('List 2 + List 4: ' + str(list2_list4_overlap_percent) + '% (' + str(int(list2_list4_overlap_total)) + ')')
    print('List 3 + List 4: ' + str(list3_list4_overlap_percent) + '% (' + str(int(list3_list4_overlap_total)) + ')')
    print('')
    print('List 1 + List 2 + List 3: ' + str(list1_list2_list3_overlap_percent) + '% (' + str(int(list1_list2_list3_overlap_total)) + ')')
    print('List 1 + List 2 + List 4: ' + str(list1_list2_list4_overlap_percent) + '% (' + str(int(list1_list2_list4_overlap_total)) + ')')
    print('List 1 + List 3 + List 4: ' + str(list1_list3_list4_overlap_percent) + '% (' + str(int(list1_list3_list4_overlap_total)) + ')')
    print('List 2 + List 3 + List 4: ' + str(list2_list3_list4_overlap_percent) + '% (' + str(int(list2_list3_list4_overlap_total)) + ')')
    print('')
    print('Shared: ' + str(all_list_overlap_percent) + '% (' + str(int(all_list_overlap_total)) + ')')

    # Return new lists
    return [list1_only,list2_only,list3_only,list4_only,list1_list2_overlap, list1_list3_overlap, list1_list4_overlap, list2_list3_overlap, list2_list4_overlap, list3_list4_overlap, list1_list2_list3_overlap, list1_list2_list4_overlap, list1_list3_list4_overlap, list2_list3_list4_overlap, all_list_overlap]


In [11]:
# Reactions
iJO1366_m9_aerobic_reactions = [x.id for x in iJO1366_m9_aerobic.model.reactions]
iJO1366_m9_anaerobic_reactions = [x.id for x in iJO1366_m9_anaerobic.model.reactions]
iJO1366_lb_aerobic_reactions = [x.id for x in iJO1366_lb_aerobic.model.reactions]
iJO1366_pfba_reactions = [x.id for x in iJO1366_pfba.model.reactions]

reactions_comparisons = venn_comparison(iJO1366_pfba_reactions, iJO1366_lb_aerobic_reactions, iJO1366_m9_aerobic_reactions, iJO1366_m9_anaerobic_reactions)

# List 1: pfba
# List 2: lb_aerobic
# List 3: m9_aerobic
# List 4: m9_anaerobic

List 1 only: 3.5% (16)
List 2 only: 1.3% (6)
List 3 only: 7.6% (37)
List 4 only: 7.4% (35)

List 1 + List 2: 7.5% (34)
List 1 + List 3: 1.3% (6)
List 1 + List 4: 1.9% (9)
List 2 + List 3: 3.4% (16)
List 2 + List 4: 2.6% (12)
List 3 + List 4: 7.9% (38)

List 1 + List 2 + List 3: 3.9% (18)
List 1 + List 2 + List 4: 2.4% (11)
List 1 + List 3 + List 4: 2.5% (12)
List 2 + List 3 + List 4: 2.3% (11)

Shared: 74.4% (347)


In [8]:
iJO1366_lb_aerobic_reactions

['DM_mththf_c',
 'BIOMASS_Ec_iJO1366_WT_53p95M',
 'EX_LalaDgluMdap_e',
 'EX_ac_e',
 'EX_ade_e',
 'EX_adn_e',
 'EX_adocbl_e',
 'EX_akg_e',
 'EX_ala__D_e',
 'EX_ala__L_e',
 'EX_alaala_e',
 'EX_arg__L_e',
 'EX_asn__L_e',
 'EX_btn_e',
 'EX_ca2_e',
 'EX_cgly_e',
 'EX_cl_e',
 'EX_co2_e',
 'EX_cobalt2_e',
 'EX_colipa_e',
 'EX_cu2_e',
 'EX_cytd_e',
 'EX_dad_2_e',
 'EX_duri_e',
 'EX_fe2_e',
 'EX_feenter_e',
 'EX_for_e',
 'EX_g3ps_e',
 'EX_gam6p_e',
 'EX_glyc_e',
 'EX_glyc3p_e',
 'EX_glyclt_e',
 'EX_gsn_e',
 'EX_gthrd_e',
 'EX_h_e',
 'EX_h2o_e',
 'EX_hdca_e',
 'EX_hdcea_e',
 'EX_his__L_e',
 'EX_ile__L_e',
 'EX_indole_e',
 'EX_k_e',
 'EX_leu__L_e',
 'EX_lipoate_e',
 'EX_lys__L_e',
 'EX_met__L_e',
 'EX_mg2_e',
 'EX_mmet_e',
 'EX_mn2_e',
 'EX_mobd_e',
 'EX_nh4_e',
 'EX_ni2_e',
 'EX_nmn_e',
 'EX_no3_e',
 'EX_o2_e',
 'EX_ocdcea_e',
 'EX_phe__L_e',
 'EX_pi_e',
 'EX_pnto__R_e',
 'EX_pro__L_e',
 'EX_ptrc_e',
 'EX_pydx_e',
 'EX_skm_e',
 'EX_so4_e',
 'EX_spmd_e',
 'EX_succ_e',
 'EX_thm_e',
 'EX_thr__L_e',

In [12]:
# Metabolites
iJO1366_m9_aerobic_metabolites = [x.id for x in iJO1366_m9_aerobic.model.metabolites]
iJO1366_m9_anaerobic_metabolites = [x.id for x in iJO1366_m9_anaerobic.model.metabolites]
iJO1366_lb_aerobic_metabolites = [x.id for x in iJO1366_lb_aerobic.model.metabolites]
iJO1366_pfba_metabolites = [x.id for x in iJO1366_pfba.model.metabolites]

metabolites_comparisons = venn_comparison(iJO1366_pfba_metabolites, iJO1366_lb_aerobic_metabolites, iJO1366_m9_aerobic_metabolites, iJO1366_m9_anaerobic_metabolites)

# List 1: pfba
# List 2: lb_aerobic
# List 3: m9_aerobic
# List 4: m9_anaerobic

List 1 only: 1.1% (5)
List 2 only: 0.2% (1)
List 3 only: 4.8% (23)
List 4 only: 3.8% (18)

List 1 + List 2: 4.0% (18)
List 1 + List 3: 0.6% (3)
List 1 + List 4: 0.6% (3)
List 2 + List 3: 1.5% (7)
List 2 + List 4: 1.3% (6)
List 3 + List 4: 4.8% (23)

List 1 + List 2 + List 3: 1.9% (9)
List 1 + List 2 + List 4: 1.5% (7)
List 1 + List 3 + List 4: 1.7% (8)
List 2 + List 3 + List 4: 1.7% (8)

Shared: 85.9% (400)


In [15]:
# Screen context specific growth rates by each model's optimal growth

# Determine bounds
pfba_obj_val_lb = iJO1366_pfba.model.slim_optimize() * 0.8
lb_aerobic_obj_val_lb = iJO1366_lb_aerobic.model.slim_optimize() * 0.8
m9_aerobic_obj_val_lb = iJO1366_m9_aerobic.model.slim_optimize() * 0.8
m9_anaerobic_obj_val_lb = iJO1366_m9_anaerobic.model.slim_optimize() * 0.8
pfba_obj_val_ub = iJO1366_pfba.model.slim_optimize()
lb_aerobic_obj_val_ub = iJO1366_lb_aerobic.model.slim_optimize()
m9_aerobic_obj_val_ub = iJO1366_m9_aerobic.model.slim_optimize()
m9_anaerobic_obj_val_ub = iJO1366_m9_anaerobic.model.slim_optimize()

# Collect fluxes
pfba_biomass = list(iJO1366_pfba.flux_samples['BIOMASS_Ec_iJO1366_WT_53p95M'])
lb_biomass = list(iJO1366_lb_aerobic.flux_samples['BIOMASS_Ec_iJO1366_WT_53p95M'])
m9_aerobic_biomass = list(iJO1366_m9_aerobic.flux_samples['BIOMASS_Ec_iJO1366_WT_53p95M'])
m9_anaerobic_biomass = list(iJO1366_m9_anaerobic.flux_samples['BIOMASS_Ec_iJO1366_WT_53p95M'])

# Screen fluxes
pfba_biomass = [x for x in pfba_biomass if x >= pfba_obj_val_lb and x <= pfba_obj_val_ub]
lb_biomass = [x for x in lb_biomass if x >= lb_aerobic_obj_val_lb and x <= lb_aerobic_obj_val_ub]
m9_aerobic_biomass = [x for x in m9_aerobic_biomass if x >= m9_aerobic_obj_val_lb and x <= m9_aerobic_obj_val_ub]
m9_anaerobic_biomass = [x for x in m9_anaerobic_biomass if x >= m9_anaerobic_obj_val_lb and x <= m9_anaerobic_obj_val_ub]

# Convert to per hour rate
pfba_rates = [round((x / 60.0), 3) for x in pfba_biomass]
lb_aerobic_rates = [round((x / 60.0), 3) for x in lb_biomass]
m9_aerobic_rates = [round((x / 60.0), 3) for x in m9_aerobic_biomass]
m9_anaerobic_rates = [round((x / 60.0), 3) for x in m9_anaerobic_biomass]

# Subsample evenly
import random
sub_level = min([len(pfba_rates), len(lb_aerobic_rates), len(m9_aerobic_rates), len(m9_anaerobic_rates)])
pfba_sub = random.sample(range(0,len(pfba_rates)), sub_level)
lb_sub = random.sample(range(0,len(lb_aerobic_rates)), sub_level)
m9a_sub = random.sample(range(0,len(m9_aerobic_rates)), sub_level)
m9n_sub = random.sample(range(0,len(m9_anaerobic_rates)), sub_level)
pfba_rates = [pfba_rates[i] for i in pfba_sub]
lb_aerobic_rates = [lb_aerobic_rates[i] for i in lb_sub]
m9_aerobic_rates = [m9_aerobic_rates[i] for i in m9a_sub]
m9_anaerobic_rates = [m9_anaerobic_rates[i] for i in m9n_sub]

# Convert to strings
pfba_rates = [str(x) for x in pfba_rates]
pfba_rates = 'base_pfba\t' + '\t'.join(pfba_rates) + '\n'
m9_aerobic_rates = [str(x) for x in m9_aerobic_rates]
m9_aerobic_rates = 'm9_gluc_aerobic\t' + '\t'.join(m9_aerobic_rates) + '\n'
m9_anaerobic_rates = [str(x) for x in m9_anaerobic_rates]
m9_anaerobic_rates = 'm9_gluc_anaerobic\t' + '\t'.join(m9_anaerobic_rates) + '\n'
lb_aerobic_rates = [str(x) for x in lb_aerobic_rates]
lb_aerobic_rates = 'lb_aerobic\t' + '\t'.join(lb_aerobic_rates) + '\n'

# Write to file
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/new_growth_rates2.tsv', 'w') as rates:
    rates.write(pfba_rates)
    rates.write(m9_aerobic_rates)
    rates.write(m9_anaerobic_rates)
    rates.write(lb_aerobic_rates)

In [21]:
# Correct the sample labels
def label_flux_samples(file_name, label):
    new_name = file_name.rstrip('tsv') + 'format.tsv'
    new_file = open(new_name, 'w')
    
    with open(file_name, 'r') as samples:
        header = samples.readline()
        header = 'sample\t' + header
        new_file.write(header)
        current = 1
        
        for line in samples:
            line = label + '_' + str(current) + '\t' + line
            new_file.write(line)
            current += 1

    new_file.close()

In [27]:
# Write chosen flux sample tables to tsvs
m9_aerobic_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/M9_aerobic.flux_samples.tsv', sep='\t')
m9_anaerobic_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/M9_anaerobic.flux_samples.tsv', sep='\t')
lb_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/LB_aerobic.flux_samples.tsv', sep='\t')
pfba_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/pFBA.flux_samples.tsv', sep='\t')
    
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/M9_aerobic.flux_samples.tsv', 'm9_aer')
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/M9_anaerobic.flux_samples.tsv', 'm9_anaer')
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/LB_aerobic.flux_samples.tsv', 'lb')
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/pFBA.flux_samples.tsv', 'pfba')

### Context-specific Essentiality

In [6]:
import cobra.flux_analysis

In [7]:
iJO1366_essential_genes = cobra.flux_analysis.find_essential_genes(iJO1366)
print('Essential genes: ' + str(len(iJO1366_essential_genes)))

Essential genes: 105


In [8]:
iJO1366_pfba_essential_genes = cobra.flux_analysis.find_essential_genes(iJO1366_pfba.model)
iJO1366_pfba_essential_genes = set([x.id for x in iJO1366_pfba_essential_genes])
print('Essential genes: ' + str(len(iJO1366_pfba_essential_genes)))

Essential genes: 233


In [27]:
iJO1366_lb_aerobic_essential_genes = cobra.flux_analysis.find_essential_genes(iJO1366_lb_aerobic.model)
iJO1366_lb_aerobic_essential_genes = set([x.id for x in iJO1366_lb_aerobic_essential_genes])
print('Essential genes: ' + str(len(iJO1366_lb_aerobic_essential_genes)))

Essential genes: 219


In [23]:
iJO1366_m9_aerobic_essential_genes = cobra.flux_analysis.find_essential_genes(iJO1366_m9_aerobic.model)
iJO1366_m9_aerobic_essential_genes = set([x.id for x in iJO1366_m9_aerobic_essential_genes])
print('Essential genes: ' + str(len(iJO1366_m9_aerobic_essential_genes)))

Essential genes: 188


In [24]:
iJO1366_m9_anaerobic_essential_genes = cobra.flux_analysis.find_essential_genes(iJO1366_m9_anaerobic.model)
iJO1366_m9_anaerobic_essential_genes = set([x.id for x in iJO1366_m9_anaerobic_essential_genes])
print('Essential genes: ' + str(len(iJO1366_m9_anaerobic_essential_genes)))

Essential genes: 217


In [25]:
essentiality_comparisons = venn_comparison(iJO1366_pfba_essential_genes, iJO1366_lb_aerobic_essential_genes, iJO1366_m9_aerobic_essential_genes, iJO1366_m9_anaerobic_essential_genes)
# List 1: pfba
# List 2: lb_aerobic
# List 3: m9_aerobic
# List 4: m9_anaerobic

List 1 only: 3.1% (7)
List 2 only: 1.8% (4)
List 3 only: 1.1% (2)
List 4 only: 6.5% (14)

List 1 + List 2: 4.9% (11)
List 1 + List 3: 2.4% (5)
List 1 + List 4: 0.5% (1)
List 2 + List 3: 0.5% (1)
List 2 + List 4: 1.8% (4)
List 3 + List 4: 1.5% (3)

List 1 + List 2 + List 3: 5.2% (11)
List 1 + List 2 + List 4: 13.1% (29)
List 1 + List 3 + List 4: 1.0% (2)
List 2 + List 3 + List 4: 2.4% (5)

Shared: 74.9% (159)


In [15]:
core_essential = iJO1366_pfba_essential_genes.intersection(iJO1366_lb_aerobic_essential_genes)
core_essential = core_essential.intersection(iJO1366_m9_aerobic_essential_genes)
core_essential = core_essential.intersection(iJO1366_m9_anaerobic_essential_genes)
print('Essential in all GENREs: ' + str(len(core_essential)))


Essential in all GENREs: 159


In [26]:
# Write individual essentiality to file
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/essentiality_supp.tsv', 'w') as outfile:
    line = 'pfba\t' + '\t'.join(list(iJO1366_pfba_essential_genes)) + '\n'
    outfile.write(line)
    line = 'pfba\t' + '\t'.join(list(iJO1366_lb_aerobic_essential_genes)) + '\n'
    outfile.write(line)
    line = 'pfba\t' + '\t'.join(list(iJO1366_m9_aerobic_essential_genes)) + '\n'
    outfile.write(line)
    line = 'pfba\t' + '\t'.join(list(iJO1366_m9_anaerobic_essential_genes)) + '\n'
    outfile.write(line)

# Find non-essentiality across models
iJO1366_pfba_genes = set([x.id for x in iJO1366_pfba.model.genes])
iJO1366_lb_aerobic_genes = set([x.id for x in iJO1366_lb_aerobic.model.genes])
iJO1366_m9_aerobic_genes = set([x.id for x in iJO1366_m9_aerobic.model.genes])
iJO1366_m9_anaerobic_genes = set([x.id for x in iJO1366_m9_anaerobic.model.genes])

# Compare overlapping genes
total_genes = set()
total_genes |= iJO1366_pfba_essential_genes
total_genes |= iJO1366_lb_aerobic_essential_genes
total_genes |= iJO1366_m9_aerobic_essential_genes
total_genes |= iJO1366_m9_anaerobic_essential_genes
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/essentiality_test.tsv', 'w') as outfile:
    outfile.write('gene\tpfba\tlb_aerobic\tm9_aerobic\tm9_anaerobic\n')
    for gene in total_genes:
        entry = ['filler','filler','filler','filler']
        
        if gene in core_essential:
            entry[0] = 3
        elif gene in iJO1366_pfba_essential_genes:
            entry[0] = 2
        elif gene in iJO1366_pfba_genes:
            entry[0] = 1
        else:
            entry[0] = 0
            
        if gene in core_essential:
            entry[1] = 3
        elif gene in iJO1366_lb_aerobic_essential_genes:
            entry[1] = 2
        elif gene in iJO1366_lb_aerobic_genes:
            entry[1] = 1
        else:
            entry[1] = 0
            
        if gene in core_essential:
            entry[2] = 3
        elif gene in iJO1366_m9_aerobic_essential_genes:
            entry[2] = 2
        elif gene in iJO1366_m9_aerobic_genes:
            entry[2] = 1
        else:
            entry[2] = 0
            
        if gene in core_essential:
            entry[3] = 3
        elif gene in iJO1366_m9_anaerobic_essential_genes:
            entry[3] = 2
        elif gene in iJO1366_m9_anaerobic_genes:
            entry[3] = 1
        else:
            entry[3] = 0
            
        entry = gene + '\t' + '\t'.join([str(x) for x in entry]) + '\n'
        outfile.write(entry)


### Benchmarking Against Previous Algorithms

In [1]:
# Load in RIPTiDe
from riptide import *

# Read in GENRE
iJO1366 = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366.xml')
iJO1366.objective = iJO1366.reactions.BIOMASS_Ec_iJO1366_WT_53p95M
for rxn in iJO1366.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (min(rxn.lower_bound, -1000.), max(rxn.upper_bound, 1000.))

# Read in experimentally essential genes - Baba et al. (2006).
#lb_crispr_essential = []
#with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/Baba2006_LB_essentiality_screen.txt', 'r') as infile:
#    for line in infile: lb_essential.append(line.strip())

# Read in formatted RNA-Seq data - aerobic M9+gluc - Monk et al. (2016)        
gpr_dict = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/iJO1366_genes.tsv', 'r') as genes:
    for line in genes:
        gpr_dict[line.split()[1]] = line.split()[0]
monk2016 = {}   
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/normalized.tsv', 'r') as transcription:
    for line in transcription:
        line = line.split()
        if line[0] == 'gene':
            continue
        else:
            try:
                gene = gpr_dict[line[0]]
            except:
                continue
            monk2016[gene] = numpy.median([int(x) for x in line[1:4]])
            

In [2]:
# Create contextualized models based on other algorithms

# CORDA
from corda import CORDA

# Define thresholds
corda_lo_threshold, corda_hi_threshold = numpy.percentile(list(monk2016.values()), [50,90])

# Format data for CORDA
corda_gene_confidences = {}
for gene in monk2016.keys():
    if monk2016[gene] < corda_lo_threshold: confidence = 0
    elif monk2016[gene] >= corda_lo_threshold and monk2016[gene] < corda_hi_threshold: confidence = 1
    elif monk2016[gene] >= corda_hi_threshold: confidence = 3
    else: confidence = -1
    corda_gene_confidences[gene] = confidence

corda_rxn_confidences = {}
corda_rxn_confidences['BIOMASS_Ec_iJO1366_WT_53p95M'] = 3
for gene in iJO1366.genes:
    try:
        confidence = corda_gene_confidences[gene.id]
    except:
        continue
    reactions = [x.id for x in list(gene.reactions)]
    for rxn in reactions:
        corda_rxn_confidences[rxn] = confidence
        
for rxn in iJO1366.reactions:
    if rxn.id not in corda_rxn_confidences.keys():
        corda_rxn_confidences[rxn.id] = 0

# Run CORDA       
optimal = CORDA(iJO1366, corda_rxn_confidences)
optimal.build()
CORDA = []
for rxn in optimal.included.keys():
    if optimal.included[rxn] == True:
        CORDA.append(rxn)
     
# Load in results from Bonnie's analysis        
GIMME = []
iMAT = []
MBA = []
RegrEx = []
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/model_reactions_Monk.txt', 'r') as infile:
    for line in infile:
        line = line.split(',')
        if line[1] == '1': GIMME.append(line[0])
        if line[2] == '1': iMAT.append(line[0])
        if line[3] == '1': MBA.append(line[0])
        if line[5] == '1': RegrEx.append(line[0])
            
GIMME = set(GIMME)
iMAT = set(iMAT)
MBA = set(MBA)
CORDA = set(CORDA)
RegrEx = set(RegrEx)

def complete_orphan_prune(model):
    removed = 1
    while removed == 1:
        removed = 0
        # Metabolites
        for cpd in model.metabolites:
            if len(cpd.reactions) == 0:
                cpd.remove_from_model(); removed = 1
        # Reactions
        for rxn in model.reactions:
            if len(rxn.metabolites) == 0: 
                rxn.remove_from_model(); removed = 1
    return model

# Prune models
warnings.filterwarnings('ignore') # Handle UserWarning
iJO1366_GIMME = copy.deepcopy(iJO1366)
for rxn in iJO1366_GIMME.reactions:
    if not rxn.id in GIMME:
        iJO1366_GIMME.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)
iJO1366_GIMME = complete_orphan_prune(iJO1366_GIMME)
iJO1366_iMAT = copy.deepcopy(iJO1366)
for rxn in iJO1366_iMAT.reactions:
    if not rxn.id in iMAT:
        iJO1366_iMAT.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)
iJO1366_iMAT = complete_orphan_prune(iJO1366_iMAT)
iJO1366_MBA = copy.deepcopy(iJO1366)
for rxn in iJO1366_MBA.reactions:
    if not rxn.id in MBA:
        iJO1366_MBA.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)
iJO1366_MBA = complete_orphan_prune(iJO1366_MBA)
iJO1366_CORDA = copy.deepcopy(iJO1366)
for rxn in iJO1366_CORDA.reactions:
    if not rxn.id in CORDA:
        iJO1366_CORDA.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)
iJO1366_CORDA = complete_orphan_prune(iJO1366_CORDA)
iJO1366_RegrEx = copy.deepcopy(iJO1366)
for rxn in iJO1366_RegrEx.reactions:
    if not rxn.id in RegrEx:
        iJO1366_RegrEx.reactions.get_by_id(rxn.id).remove_from_model(remove_orphans=True)
iJO1366_RegrEx = complete_orphan_prune(iJO1366_RegrEx)
warnings.filterwarnings('default')

iJO1366_RIPTiDe = riptide.contextualize(iJO1366, transcriptome=monk2016, silent=True)

In [6]:
# Function to identify essential genes
def essentiality_screen(model):
    
    # Check the model grows at all
    essential_genes = set()
    if str(model.slim_optimize()) == 'nan' or model.slim_optimize() <= 1e-6:
        print('WARNING: No objective flux found!')
        return essential_genes
    else:
        # Close all reactions associated with each gene iteratively
        essential_genes = set()
        for gene in model.genes:
            old_bounds = {}
            for rxn in gene.reactions:
                old_bounds[rxn.id] = rxn.bounds
                rxn.bounds = (0.0,0.0)

            # Test growth levels
            test = model.slim_optimize()
            if str(test) == 'nan' or test <= 1e-6:
                essential_genes |= set([gene.id])

            # Reset reaction bounds
            for rxn in old_bounds.keys():
                model.reactions.get_by_id(rxn).bounds = old_bounds[rxn]

        return essential_genes


In [7]:
# Calculate new gene essentiality
base_essential = essentiality_screen(iJO1366)
GIMME_essential = essentiality_screen(iJO1366_GIMME)
iMAT_essential = essentiality_screen(iJO1366_iMAT)
MBA_essential = essentiality_screen(iJO1366_MBA)
CORDA_essential = essentiality_screen(iJO1366_CORDA)
RegrEx_essential = essentiality_screen(iJO1366_RegrEx)
RIPTiDe_essential = essentiality_screen(iJO1366_RIPTiDe.model)

In [34]:
iJO1366

<Model iJO1366 at 0x7fdd22650c10>

In [35]:
len(iJO1366.genes)

1367

In [40]:
print('base model objective value: ' + str(iJO1366.slim_optimize()))
print('base model essential genes: ' + str(len(base_essential)))

base model objective value: 105.76529080812094
base model essential genes: 152


In [8]:
iJO1366_GIMME

<Model iJO1366 at 0x7fdd3dd7d2d0>

In [41]:
len(iJO1366_GIMME.genes)

1077

In [27]:
print('GIMME model objective value: ' + str(iJO1366_GIMME.slim_optimize()))
print('GIMME model essential genes: ' + str(len(GIMME_essential)))

GIMME model objective value: 83.53363814358377
GIMME model essential genes: 215


In [11]:
iJO1366_iMAT

<Model iJO1366 at 0x7fdd21fc0a90>

In [28]:
len(iJO1366_iMAT.genes)

1027

In [29]:
print('iMAT model objective value: ' + str(iJO1366_iMAT.slim_optimize()))
print('iMAT model essential genes: ' + str(len(iMAT_essential)))

iMAT model objective value: 0.0
iMAT model essential genes: 0


In [13]:
iJO1366_MBA

<Model iJO1366 at 0x7fdd3e598410>

In [30]:
len(iJO1366_MBA.genes)

1069

In [14]:
print('MBA model objective value: ' + str(iJO1366_MBA.slim_optimize()))
print('MBA model essential genes: ' + str(len(MBA_essential)))

MBA model objective value: 0.0
MBA model essential genes: 0


In [15]:
iJO1366_CORDA

<Model iJO1366 at 0x7fdd3e499d50>

In [31]:
len(iJO1366_CORDA.genes)

1062

In [16]:
print('CORDA model objective value: ' + str(iJO1366_CORDA.slim_optimize()))
print('CORDA model essential genes: ' + str(len(CORDA_essential)))

CORDA model objective value: 91.59845685323275
CORDA model essential genes: 188


In [17]:
iJO1366_RegrEx

<Model iJO1366 at 0x7fdd3e0bd810>

In [32]:
len(iJO1366_RegrEx.genes)

869

In [18]:
print('RegrEx model objective value: ' + str(iJO1366_RegrEx.slim_optimize()))
print('RegrEx model essential genes: ' + str(len(RegrEx_essential)))

RegrEx model objective value: nan
RegrEx model essential genes: 0


In [19]:
iJO1366_RIPTiDe.model

<Model iJO1366_riptide at 0x7fdd214a6e90>

In [33]:
len(iJO1366_RIPTiDe.model.genes)

378

In [20]:
print('RIPTiDe model objective value: ' + str(iJO1366_RIPTiDe.model.slim_optimize()))
print('RIPTiDe model essential genes: ' + str(len(RIPTiDe_essential)))

RIPTiDe model objective value: 84.74266887508165
RIPTiDe model essential genes: 338


### Gene Essentiality Comparison to CRISPr screen

In [31]:
# Compare with experimental CRISPr screen in LB rich media
lb_essential = []
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/Baba2006_LB_essentiality_screen.txt', 'r') as infile:
    for line in infile:
        lb_essential.append(line.strip())
        
# Screen for those genes in base iJO1366 model
invitro_lb_essential = []
for gene in iJO1366.genes:
    if gene.id in lb_essential:
        invitro_lb_essential.append(gene.id)
invitro_lb_essential = set(invitro_lb_essential)
print('CRISPr screen essential genes: ' + str(len(invitro_lb_essential)))

# Screen for essentiality in base model with corrected media exchanges
lb_exchanges = ['EX_ala_e','EX_arg_e','EX_asp_e','EX_cys_e','EX_glu_e','EX_gly_e','EX_his_e','EX_ile_e',
                'EX_leu_e','EX_lys_e','EX_met_e','EX_pro_e','EX_thr_e','EX_tyr_e','EX_phe_e','EX_ser_e',
                'EX_trp_e','EX_val_e','EX_pnto_e','EX_nac_e','EX_na1_e','EX_cl_e','EX_so4_e','EX_k_e',
                'EX_pi_e','EX_ca2_e','EX_mg2_e','EX_zn2_e','EX_aso3_e','EX_cd2_e','EX_hg2_e','EX_h_e',
                'EX_h2o_e','EX_o2_e','EX_ins_e','EX_hxan_e','EX_dcyt_e','EX_thymd_e','EX_ura_e',
                'EX_uri_e','EX_dad_e','EX_adn_e','EX_co2_e','EX_cobalt2_e','EX_cu2_e','EX_fe2_e',
                'EX_fe3_e','EX_mn2_e','EX_mobd_e','EX_tungs_e','EX_cbl1_e','EX_fru_e','EX_gal_e',
                'EX_ni2_e','EX_sel_e','EX_slnt_e','EX_adocbl_e','EX_cobalt2_e','EX_cu2_e','EX_fe3dcit_e',
                'EX_mn2_e','EX_mobd_e','EX_ni2_e','EX_zn2_e']

other_exchanges = []
for rxn in iJO1366.reactions:
    if len(rxn.products) == 0:
        if not rxn.id in lb_exchanges:
            rxn.bounds = (0., min([rxn.upper_bound, 1000.]))
            other_exchanges.append(rxn.id)
insilico_lb_essential = essentiality_screen(iJO1366)
for rxn in other_exchanges: iJO1366.reactions.get_by_id(rxn).bounds = (-1000.,1000)
print('Base model essential genes: ' + str(len(insilico_lb_essential)))

correct_essential = insilico_lb_essential.intersection(invitro_lb_essential)
print('Agreement essential genes: ' + str(len(correct_essential)))
print('\n')

invitro_lb_essential = correct_essential

overlap_base_essential = base_essential.intersection(invitro_lb_essential)
base_only = base_essential.difference(invitro_lb_essential)
baba_base_only = invitro_lb_essential.difference(RIPTiDe_essential)

# Report results
print('Overlap: ' + str(len(overlap_base_essential)))
print('Base model only: ' + str(len(base_only)) + ' (' + str(round((len(base_only)/(len(base_only)+len(overlap_base_essential)))*100.,2)) + '%)')
print('in vitro only: ' + str(len(baba_base_only)) + ' (' + str(round((len(baba_base_only)/(len(baba_base_only)+len(overlap_base_essential)))*100.,2)) + '%)')
print('\n')

#------------------------------------------------#

# Compare with RIPTiDe results
overlap_riptide_essential = RIPTiDe_essential.intersection(invitro_lb_essential)
riptide_only = RIPTiDe_essential.difference(invitro_lb_essential)
baba_only = invitro_lb_essential.difference(RIPTiDe_essential)

# Report results
print('Overlap: ' + str(len(overlap_riptide_essential)))
print('RIPTiDe only: ' + str(len(riptide_only)) + ' (' + str(round((len(riptide_only)/(len(riptide_only)+len(overlap_riptide_essential)))*100.,2)) + '%)')
print('in vitro only: ' + str(len(baba_only)) + ' (' + str(round((len(baba_only)/(len(baba_only)+len(overlap_riptide_essential)))*100.,2)) + '%)')
print('\n')

# Compare with CORDA results
overlap_corda_essential = CORDA_essential.intersection(invitro_lb_essential)
corda_only = CORDA_essential.difference(invitro_lb_essential)
baba_corda_only = invitro_lb_essential.difference(CORDA_essential)

# Report results
print('Overlap: ' + str(len(overlap_corda_essential)))
print('CORDA only: ' + str(len(corda_only)) + ' (' + str(round((len(corda_only)/(len(corda_only)+len(overlap_corda_essential)))*100.,2)) + '%)')
print('in vitro only: ' + str(len(baba_corda_only)) + ' (' + str(round((len(baba_corda_only)/(len(baba_corda_only)+len(overlap_corda_essential)))*100.,2)) + '%)')
print('\n')

# Compare in silico results
overlap_insilico = CORDA_essential.intersection(RIPTiDe_essential)
corda_insilico_only = CORDA_essential.difference(RIPTiDe_essential)
riptide_insilico_only = RIPTiDe_essential.difference(CORDA_essential)

# Report results
print('Overlap: ' + str(len(overlap_insilico)))
print('CORDA only: ' + str(len(corda_insilico_only)) + ' (' + str(round((len(corda_insilico_only)/(len(corda_insilico_only)+len(overlap_insilico)))*100.,2)) + '%)')
print('RIPTiDe only: ' + str(len(riptide_insilico_only)) + ' (' + str(round((len(riptide_insilico_only)/(len(riptide_insilico_only)+len(overlap_insilico)))*100.,2)) + '%)')


CRISPr screen essential genes: 137
Base model essential genes: 336
Agreement essential genes: 96


Overlap: 62
Base model only: 90 (59.21%)
in vitro only: 32 (34.04%)


Overlap: 64
RIPTiDe only: 292 (82.02%)
in vitro only: 32 (33.33%)


Overlap: 71
CORDA only: 128 (64.32%)
in vitro only: 25 (26.04%)


Overlap: 173
CORDA only: 26 (13.07%)
RIPTiDe only: 183 (51.4%)


### Inferring media condition

In [20]:
# Read in formatted RNA-Seq data - Lybecker et al. (2014).
lb_aerobic = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Lybecker_2014.mapped.norm.tsv', 'r') as transcription:
    header = transcription.readline()
    for line in transcription:
        gene = line.strip().split()[0]
        abundance = float(line.strip().split()[1])
        lb_aerobic[gene] = abundance
        
gpr_dict = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/iJO1366_genes.tsv', 'r') as genes:
    for line in genes:
        gpr_dict[line.split()[1]] = line.split()[0]
m9_aerobic = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Monk_et_al_2016/normalized.tsv', 'r') as transcription:
    for line in transcription:
        line = line.split()
        if line[0] == 'gene': continue
        try:
            gene = gpr_dict[line[0]]
        except:
            continue
        m9_aerobic[gene] = numpy.median([int(x) for x in line[1:4]])
            
iJO1366_RIPTiDe = riptide.contextualize(iJO1366, transcriptome=lb_aerobic, silent=True)
RIPTiDe_LB_exchanges = set([x.id for x in iJO1366_RIPTiDe.model.reactions if 'EX_' in x.id])
iJO1366_RIPTiDe = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, silent=True)
RIPTiDe_M9_exchanges = set([y.id for y in iJO1366_RIPTiDe.model.reactions if 'EX_' in y.id])
base_exchanges = set([x.id for x in iJO1366.reactions if 'EX_' in x.id])

pruned_exchanges = base_exchanges.difference(RIPTiDe_LB_exchanges)
pruned_ratio = (float(len(pruned_exchanges)) / float(len(base_exchanges))) * 100.
pruned_ratio = round(pruned_ratio, 2)
print('LB')
print('Total pruned: ' + str(len(pruned_exchanges)) + ' (' + str(pruned_ratio) + '%)')
print('Included exchange reactions: ' + str(len(RIPTiDe_LB_exchanges)))

pruned_exchanges = base_exchanges.difference(RIPTiDe_M9_exchanges)
pruned_ratio = (float(len(pruned_exchanges)) / float(len(base_exchanges))) * 100.
pruned_ratio = round(pruned_ratio, 2)
print('\nM9')
print('Total pruned: ' + str(len(pruned_exchanges)) + ' (' + str(pruned_ratio) + '%)')
print('Included exchange reactions: ' + str(len(RIPTiDe_M9_exchanges)))

lb_only = RIPTiDe_LB_exchanges.difference(RIPTiDe_M9_exchanges)
m9_only = RIPTiDe_M9_exchanges.difference(RIPTiDe_LB_exchanges)
print('\nLB only: ' + str(len(lb_only)))
print('M9 only: ' + str(len(m9_only)))

LB
Total pruned: 253 (78.09%)
Included exchange reactions: 71

M9
Total pruned: 250 (77.16%)
Included exchange reactions: 74

LB only: 13
M9 only: 16


In [21]:
for x in lb_only:
    print(iJO1366.reactions.get_by_id(x).reactants[0].name)

Glycerol 3-phosphate
Glycerophosphoserine
Cys Gly C5H10N2O3S
Deoxyuridine
L-Isoleucine
D-Alanine
Phosphate
Nitrate
L-Aspartate
L-Valine
L-Methionine
Indole
Guanosine


In [22]:
for x in m9_only:
    print(iJO1366.reactions.get_by_id(x).reactants[0].name)

Thymidine C10H14N2O5
L-Tryptophan
Xanthosine
Citrate
L-Serine
L-Malate
L-Methionine Sulfoxide
Guanine
Xanthine
Ethanolamine
Cu+
Pyruvate
Hypoxanthine
L-Cysteine
D-Glucose 6-phosphate
D-Fructose 6-phosphate


In [267]:
# RIPTiDe - LB
lb_aerobic = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Lybecker_2014.mapped.norm.tsv', 'r') as transcription:
    header = transcription.readline()
    for line in transcription:
        gene = line.strip().split()[0]
        abundance = float(line.strip().split()[1])
        lb_aerobic[gene] = abundance
        
iJO1366_RIPTiDe = riptide.contextualize(iJO1366, transcriptome=lb_aerobic, silent=True)
RIPTiDe_exchanges = []
for rxn in iJO1366_RIPTiDe.model.reactions:
    if len(rxn.products) == 0:
        RIPTiDe_exchanges.append(rxn.id)
RIPTiDe_exchanges = set(RIPTiDe_exchanges)
RIPTiDe_substrates = []
for rxn in RIPTiDe_exchanges:
    flux = iJO1366_RIPTiDe.flux_samples[rxn]
    flux = round(numpy.median(flux), 3)
    if flux < 0.0:
        substrate = iJO1366_RIPTiDe.model.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
        RIPTiDe_substrates.append([substrate, flux])
RIPTiDe_substrates = pandas.DataFrame.from_records(RIPTiDe_substrates)
RIPTiDe_substrates.columns = ['Metabolite', 'Median_exchange_flux']

RIPTiDe_substrates.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/results/tables/RIPTiDe_LB_substrates.tsv', sep='\t', index=False)

In [269]:
# M9 aerobic
iJO1366_RIPTiDe = riptide.contextualize(iJO1366, transcriptome=m9_aerobic, silent=True)
RIPTiDe_M9_exchanges = set([x.id for x in iJO1366_RIPTiDe.model.reactions if 'EX_' in x.id])
RIPTiDe_M9_exchanges = list(RIPTiDe_M9_exchanges)

with open('/home/mjenior/Desktop/m9_media.tsv', 'w') as m9_media:
    for rxn in RIPTiDe_M9_exchanges:
        flux = iJO1366_RIPTiDe.flux_samples[rxn]
        flux = round(numpy.median(flux), 3)
        if flux < 0.0:
            substrate = iJO1366.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
            entry = substrate + '\t' + rxn + '\t' + str(flux) + '\n'
            m9_media.write(entry)
        

In [27]:
# Other models/algorithms
import numpy
import pandas


def gapsplit(model, n=500):

    # Define a few more variables
    max_tries=1000
    primary_tol=0.001
    secondary_frac=0.05
    min_range=1e-5
    enforce_range=True

    warnings.filterwarnings('ignore') # Handle uninformative infeasible warning

    reactions = model.reactions
    fva = flux_variability_analysis(model, reactions, fraction_of_optimum=0.001)

    if secondary_frac >= 1.0:
        n_secondary = secondary_frac
    else:
        n_secondary = numpy.floor(secondary_frac * len(model.reactions)).astype(int)

    # only split reactions with feasible range >= min_range
    idxs = (fva.maximum - fva.minimum >= min_range).to_numpy().nonzero()[0]
    weights = (1.0 / (fva.maximum - fva.minimum) ** 2).to_numpy()

    samples = numpy.zeros((n, len(model.reactions)))
    k = 0
    infeasible_count = 0

    for try_ in range(max_tries):
        relative, target, width = _maxgap(samples[0:k,idxs], fva.iloc[idxs,:])
        
        primary_var = numpy.argmax(relative)
        primary_target = target[primary_var]
        primary_lb = primary_target - primary_tol*width[primary_var]
        primary_ub = primary_target + primary_tol*width[primary_var]

        secondary_vars = numpy.random.choice(len(idxs), n_secondary, replace=False)
        secondary_targets = target[secondary_vars]
        secondary_weights = weights[idxs[secondary_vars]]

        new_sample = _generate_sample(
            model, idxs[primary_var], primary_lb, primary_ub,
            idxs[secondary_vars], secondary_targets, secondary_weights)
        if new_sample is not None:
            if enforce_range:
                new_sample[new_sample > fva.maximum] = fva.maximum[new_sample > fva.maximum]
                new_sample[new_sample < fva.minimum] = fva.minimum[new_sample < fva.minimum]

            samples[k,:] = new_sample
            k += 1
        else:
            infeasible_count += 1

        if k >= n: break

    if k < n:
        # max_tries reached; return fewer than n samples
        samples = samples[:k,:]

    warnings.filterwarnings('default') # Return warnings to previous settings
    return pandas.DataFrame(data=samples,columns=fva.maximum.index)


def _generate_sample(
        model, primary_var, primary_lb, primary_ub,
        secondary_vars=None, secondary_targets=None, secondary_weights=None):
    
    # Formulate a [MI]QP to find a single solution
    with model:
        model.reactions[primary_var].lower_bound = primary_lb
        model.reactions[primary_var].upper_bound = primary_ub
        model.objective = symengine.RealDouble(0)
        solution = model.optimize()
        if solution.status != 'optimal':
            return None
        else:
            return solution.fluxes


def _maxgap(points, fva):
    points = points.copy()
    points = numpy.vstack((fva.minimum, points, fva.maximum))
    points.sort(0)

    gaps = points[1:,:] - points[0:-1,:]
    width = gaps.max(0)
    loc = gaps.argmax(0)
    left = numpy.zeros(width.size)
    for i in range(width.size):
        left[i] = points[loc[i],i]

    relative = width / (points[-1,:] - points[0,:])
    target = left + width / 2.0

    return relative, target, width


#--------------------------------------------------------------#

# Base model
base_samples = gapsplit(iJO1366)
base_exchanges = []
for rxn in iJO1366.reactions:
    if len(rxn.products) == 0:
        base_exchanges.append(rxn.id)
base_exchanges = set(base_exchanges)
base_substrates = []
for rxn in base_exchanges:
    flux = base_samples[rxn]
    flux = round(numpy.median(flux), 3)
    if flux < 0.0:
        substrate = iJO1366.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
        base_substrates.append([substrate, flux])
base_substrates = pandas.DataFrame.from_records(base_substrates)
base_substrates.columns = ['Metabolite', 'Median_exchange_flux']

# RIPTiDe
RIPTiDe_exchanges = []
for rxn in iJO1366_RIPTiDe.model.reactions:
    if len(rxn.products) == 0:
        RIPTiDe_exchanges.append(rxn.id)
RIPTiDe_exchanges = set(RIPTiDe_exchanges)
RIPTiDe_substrates = []
for rxn in RIPTiDe_exchanges:
    flux = iJO1366_RIPTiDe.flux_samples[rxn]
    flux = round(numpy.median(flux), 3)
    if flux < 0.0:
        substrate = iJO1366_RIPTiDe.model.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
        RIPTiDe_substrates.append([substrate, flux])
RIPTiDe_substrates = pandas.DataFrame.from_records(RIPTiDe_substrates)
RIPTiDe_substrates.columns = ['Metabolite', 'Median_exchange_flux']

# GIMME
GIMME_samples = gapsplit(iJO1366_GIMME)
GIMME_exchanges = []
for rxn in iJO1366_GIMME.reactions:
    if len(rxn.products) == 0:
        GIMME_exchanges.append(rxn.id)
GIMME_exchanges = set(GIMME_exchanges)
GIMME_substrates = []
for rxn in GIMME_exchanges:
    flux = GIMME_samples[rxn]
    flux = round(numpy.median(flux), 3)
    if flux < 0.0:
        substrate = iJO1366_GIMME.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
        GIMME_substrates.append([substrate, flux])
GIMME_substrates = pandas.DataFrame.from_records(GIMME_substrates)
GIMME_substrates.columns = ['Metabolite', 'Median_exchange_flux']

# CORDA
CORDA_samples = gapsplit(iJO1366_CORDA)
CORDA_exchanges = []
for rxn in iJO1366_CORDA.reactions:
    if len(rxn.products) == 0:
        CORDA_exchanges.append(rxn.id)
CORDA_exchanges = set(CORDA_exchanges)
CORDA_substrates = []
for rxn in CORDA_exchanges:
    flux = CORDA_samples[rxn]
    flux = round(numpy.median(flux), 3)
    if flux < 0.0:
        substrate = iJO1366_CORDA.reactions.get_by_id(rxn).reactants[0].name.replace(' ','_')
        CORDA_substrates.append([substrate, flux])
CORDA_substrates = pandas.DataFrame.from_records(CORDA_substrates)
CORDA_substrates.columns = ['Metabolite', 'Median_exchange_flux']


In [28]:
base_substrates

Metabolite  Echange_flux
0          Trimethylamine_N-oxide     -1000.000
1                         Nitrate     -1000.000
2                            Zinc        -0.001
3                    UDPgalactose      -713.185
4                       Potassium        -0.368
5                      L-Arginine        -0.453
6                       Manganese        -0.001
7                     L-Glutamine       -93.538
8                  2-Oxoglutarate      -484.320
9              1,4-alpha-D-glucan       -29.971
10                    D-Gluconate     -1000.000
11                        Calcium        -0.010
12                          O2_O2     -1000.000
13                      Magnesium        -0.016
14                     L-tartrate     -1000.000
15                        Ethanol      -991.322
16                            Cu+     -1000.000
17                       Hydrogen     -1000.000
18                       Chloride        -0.010
19                         Indole     -1000.000
20           Glycerophosphoserine        -1.573
21                         Nickel        -0.001
22                    L-Glutamate     -1000.000
23  Myo-Inositol_hexakisphosphate      -113.292

In [29]:
RIPTiDe_substrates

Metabolite  Exchange_flux
0                                      Deoxyadenosine       -550.084
1                                           Shikimate         -0.122
2                                           Molybdate         -0.009
3                                     L-Phenylalanine        -12.291
4                                        Ethanolamine       -157.761
5                                              Nickel         -0.021
6                               D-Glucose_6-phosphate        -10.528
7                                             Guanine        -16.151
8                                          Spermidine         -0.460
9                                          L-Tyrosine         -9.149
10                                        L-Threonine        -76.706
11                                           Cytidine        -10.612
12                            Hexadecanoate_(n-C16:0)         -8.282
13                                          Pyridoxal         -0.015
14                                          Potassium        -12.678
15                             L-Methionine_Sulfoxide        -10.120
16                                          Manganese         -0.045
17                                           L-Serine        -20.932
18                                              O2_O2       -802.048
19                                           Chloride         -0.338
20                                          Adenosine        -13.616
21                              S-Methyl-L-methionine         -0.091
22  L-alanine-D-glutamate-meso-2,6-diaminoheptaned...         -1.883
23                                               Co2+         -0.002
24                                         L-Arginine        -19.624
25                                            Thiamin         -0.015
26                                            Uridine         -9.566
27                                  Fe2+_mitochondria         -1.045
28                                          L-Proline        -14.666
29                                            Sulfate         -0.282
30                                  Adenosylcobalamin         -0.015
31                             D-Fructose_6-phosphate        -46.628
32                                           L-Lysine        -22.767
33                                    Fe-enterobactin         -0.015
34                                         Putrescine         -2.272
35                                                Cu+       -534.158
36                            Octadecenoate_(n-C18:1)         -3.320
37                                     2-Oxoglutarate       -980.255
38                               Thymidine_C10H14N2O5         -1.694
39                                               Zinc         -0.022
40                                          L-Leucine        -29.890
41                                         Xanthosine       -204.204
42                                            Calcium         -0.338
43                                    NMN_C11H14N2O8P         -0.156
44                            Hexadecenoate_(n-C16:1)         -6.442
45                                Reduced_glutathione         -0.015
46                                        L-Histidine         -6.285
47                                           L-Malate        -16.084
48                                         L-Cysteine         -6.220
49                                            Nitrite       -230.709
50                          D-Glucosamine_6-phosphate         -3.766
51                                          Magnesium         -0.563
52                                       L-Asparagine        -15.993
53                                       L-Tryptophan         -3.771
54                                   (R)-Pantothenate         -0.039
55                       Core_oligosaccharide_lipid_A         -0.557

In [30]:
GIMME_substrates

Metabolite  Exchange_flux
0          Trimethylamine_N-oxide      -1000.000
1                       Potassium         -0.016
2                     L-Threonine       -516.765
3                     L-Glutamine        -35.846
4                  2-Oxoglutarate       -176.134
5              Dimethyl_sulfoxide       -759.332
6                        L-Serine       -641.787
7                           O2_O2      -1000.000
8                       Magnesium         -0.001
9                        Hydrogen      -1000.000
10                    L-Glutamate       -332.060
11  Meso-2,6-Diaminoheptanedioate         -0.262

In [31]:
CORDA_substrates

Metabolite  Exchange_flux
0                               L-alanine-L-glutamate        -27.589
1                                               O2_O2       -763.577
2                                            L-Valine         -0.039
3                                              Indole      -1000.000
4                                         L-Histidine         -0.009
5                             Hexadecanoate_(n-C16:0)         -1.325
6                                             Nitrate       -482.231
7                                 Reduced_glutathione         -0.010
8                                           Magnesium         -0.001
9                                          L-tartrate       -126.039
10                       Core_oligosaccharide_lipid_A         -0.001
11  L-alanine-D-glutamate-meso-2,6-diaminoheptaned...         -0.003
12                                    L-Phenylalanine         -0.017
13                                         L-Tyrosine         -0.013
14                                        L-Threonine      -1000.000
15                                       L-Isoleucine         -0.027
16                                            Citrate        -95.847
17                                          Potassium         -0.018
18                                  Butyrate_(n-C4:0)       -992.591
19                                 D-Alanyl-D-alanine         -7.039

In [37]:
# Create supplementary table
base_substrates.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/results/tables/base_substrates.tsv', sep='\t', index=False)
RIPTiDe_substrates.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/results/tables/RIPTiDe_substrates.tsv', sep='\t', index=False)
GIMME_substrates.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/results/tables/GIMME_substrates.tsv', sep='\t', index=False)
CORDA_substrates.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/results/tables/CORDA_substrates.tsv', sep='\t', index=False)

### Metatranscriptomic analysis

In [21]:
def find_source(model, flux_samples, met_id):
    generating = set()
    for rxn in model.reactions:
        for met in rxn.products:
            if met_id in met.id:
                generating |= set([rxn.id])
    
    screened = []
    for rxn in generating:
        if numpy.median(flux_samples[rxn]) > 0:
            screened.append(rxn)
            
    print('Metabolite sources: ' + str(len(screened)))
    return screened

In [3]:
clinda_k12_metaT = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/clinda_k12.mapped.norm.tsv', 'r') as transcription:
    header = transcription.readline()
    for line in transcription:
        line = line.split()
        clinda_k12_metaT[line[0]] = float(line[2])

In [11]:
iJO1366_invivo = riptide.contextualize(iJO1366, transcriptome=clinda_k12_metaT)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 452 from 2583 (82.5% change)
Metabolites pruned to 453 from 1805 (74.9% change)
Flux through the objective DECREASED to ~87.01 from ~105.77 (17.74% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 1 minutes and 40 seconds



In [52]:
# Need to save coefficients for plotting
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/clinda_k12.weights.tsv', 'w') as weights:
    for index in iJO1366_invivo.minimization_coefficients.keys():
        line = index + '\t' + str(iJO1366_invivo.minimization_coefficients[index]) + '\n'
        weights.write(line)


In [10]:
m9_aerobic_samples = iJO1366_m9_aerobic.flux_samples
m9_anaerobic_samples = iJO1366_m9_anaerobic.flux_samples
lb_samples = iJO1366_lb_aerobic.flux_samples
invivo_samples = iJO1366_invivo.flux_samples

m9_aerobic_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/media_conditions/M9_aerobic.flux_samples.tsv', sep='\t')
m9_anaerobic_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/media_conditions/M9_anaerobic.flux_samples.tsv', sep='\t')
lb_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/media_conditions/LB_aerobic.flux_samples.tsv', sep='\t')
invivo_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/media_conditions/invivo.flux_samples.tsv', sep='\t')

In [29]:
invivo_rates = collect_growth_rates(invivo_metaT_samples, 'BIOMASS_Ec_iJO1366_WT_53p95M')
print([min(invivo_rates), numpy.median(invivo_rates), max(invivo_rates)])
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/invivo_growth_rates.tsv', 'w') as output_file:
    for x in invivo_rates: output_file.write(str(x) + '\n')

[0.538, 0.578, 0.886]


In [12]:
invivo_anaerobic_atp = find_source(iJO1366_invivo.model, 'atp_c')

Metabolite sources: 3


In [54]:
vitro_ex = set([x.id for x in iJO1366_m9_anaerobic.model.reactions if 'EX_' in x.id])
vivo_ex = set([x.id for x in iJO1366_invivo.model.reactions if 'EX_' in x.id])

vitro_ex_only = vitro_ex.difference(vivo_ex)
vitro_ex_only_input = set()
for y in vitro_ex_only:
    if abs(iJO1366_m9_anaerobic.reactions.get_by_id(y).lower_bound) > abs(iJO1366_m9_anaerobic.reactions.get_by_id(y).upper_bound):
        vitro_ex_only_input |= set([y])

vivo_ex_only = vivo_ex.difference(vitro_ex)
vivo_ex_only_input = set()
for y in vivo_ex_only:
    if abs(iJO1366_invivo_metaT.reactions.get_by_id(y).lower_bound) > abs(iJO1366_invivo_metaT.reactions.get_by_id(y).upper_bound):
        vivo_ex_only_input |= set([y])

In [58]:
for x in vitro_ex_only_input: print(iJO1366_m9_anaerobic.reactions.get_by_id(x).reactants[0].name)

Quinate
Glycerol 3-phosphate
Glycerophosphoserine
L-Leucine
L-tartrate
Ethanol
Guanosine
D-Fructose 6-phosphate
Allantoin


In [59]:
for x in vivo_ex_only_input: print(iJO1366_invivo_metaT.reactions.get_by_id(x).reactants[0].name)

L-Serine
Deoxyuridine
Trehalose
Deoxyguanosine
Glycine
Pyridoxine
Myo-Inositol hexakisphosphate
Shikimate


In [19]:
max_doubling_time(iJO1366_invivo_metaT)

1.11 hours


In [22]:
# Write flux sample tables to tsv
m9_anaerobic_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/invitro.flux_samples.tsv', sep='\t')
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/invitro.flux_samples.tsv', 'invitro')

invivo_metaT_samples.to_csv('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/invivo.flux_samples.tsv', sep='\t')
label_flux_samples('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/flux_samples/invivo.flux_samples.tsv', 'invivo')

In [17]:
invivo_metaT_times = collect_doubling_times(invivo_metaT_samples, 'BIOMASS_Ec_iJO1366_WT_53p95M')
print([min(invivo_metaT_times), numpy.median(invivo_metaT_times), max(invivo_metaT_times)])
invivo_metaT_rates = collect_growth_rates(invivo_metaT_samples, 'BIOMASS_Ec_iJO1366_WT_53p95M')
print([min(invivo_metaT_rates), numpy.median(invivo_metaT_rates), max(invivo_metaT_rates)])

[86.41, 105.13, 111.6]
[0.538, 0.571, 0.694]


### NADPH sources

In [22]:
m9_nadph = find_source(iJO1366_m9_aerobic.model, iJO1366_m9_aerobic.flux_samples, 'nadph_c')
lb_nadph = find_source(iJO1366_lb_aerobic.model, iJO1366_lb_aerobic.flux_samples, 'nadph_c')

Metabolite sources: 2
Metabolite sources: 2


In [23]:
m9_nadph

['THD2pp', 'MTHFD']

In [24]:
lb_nadph

['MTHFD', 'G3PD2']

In [5]:
# Check transcription levels
def normalize_abundance(gene, transcription_dict):
    total_transcript = float(sum(transcription_dict.values()))
    new_abund = (transcription_dict[gene] / total_transcript) * 1000000.0 # RPM normalize
    return str(int(round(new_abund)))

print('M9 aerobic')
print('THD2pp = b1602 (pntB): ' + normalize_abundance('b1602', m9_aerobic))
print('THD2pp = b1603 (pntA): ' + normalize_abundance('b1603', m9_aerobic))
print('G3PD2 = b3608 (gpsA): ' + normalize_abundance('b3608', m9_aerobic))

print('MTHFD = b0529 (folD): ' + normalize_abundance('b0529', m9_aerobic))
print('\n')

print('LB aerobic')
print('THD2pp = b1602 (pntB): ' + normalize_abundance('b1602', lb_aerobic))
print('THD2pp = b1603 (pntA): ' + normalize_abundance('b1603', lb_aerobic))
print('G3PD2 = b3608 (gpsA): ' + normalize_abundance('b3608', lb_aerobic))

print('MTHFD = b0529 (folD): ' + normalize_abundance('b0529', lb_aerobic))


M9 aerobic
THD2pp = b1602 (pntB): 4507
THD2pp = b1603 (pntA): 5857
G3PD2 = b3608 (gpsA): 834
MTHFD = b0529 (folD): 522


LB aerobic
THD2pp = b1602 (pntB): 433
THD2pp = b1603 (pntA): 505
G3PD2 = b3608 (gpsA): 467
MTHFD = b0529 (folD): 361


In [15]:
numpy.sum(list(m9_aerobic.values()))

532678.0

In [16]:
numpy.sum(list(lb_aerobic.values()))

47449.8973

### Testing Previous Integration Algorithms

In [179]:
# Comparison to GIMME, iMAT, and CORDA
import copy
import cobra
from corda import CORDA

In [181]:
iJO1366 = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iJO1366.xml')
iJO1366.objective = iJO1366.reactions.BIOMASS_Ec_iJO1366_WT_53p95M

# Open all exchanges
exchanges = set()
for rxn in iJO1366.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000, 1000)
        exchanges |= set([rxn.id])

In [208]:
# CORDA
from corda import CORDA

# Read in formatted data
lybecker2014 = {}
with open('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/transcript/Lybecker_2014.mapped.norm.tsv', 'r') as transcription:
    header = transcription.readline()
    for line in transcription:
        gene = line.strip().split()[0]
        abundance = float(line.strip().split()[1])
        lybecker2014[gene] = abundance

# Define thresholds
corda_lo_threshold, corda_hi_threshold = numpy.percentile(list(lybecker2014.values()), [50 ,75])

# Format data for CORDA
corda_gene_confidences = {}
for gene in lybecker2014.keys():
    if lybecker2014[gene] < corda_lo_threshold: confidence = 0
    elif lybecker2014[gene] >= corda_lo_threshold and lybecker2014[gene] < corda_hi_threshold: confidence = 1
    elif lybecker2014[gene] >= corda_hi_threshold: confidence = 3
    else: confidence = -1
    corda_gene_confidences[gene] = confidence

corda_rxn_confidences = {}
corda_rxn_confidences['BIOMASS_Ec_iJO1366_WT_53p95M'] = 3
for gene in iJO1366.genes:
    try:
        confidence = corda_gene_confidences[gene.id]
    except:
        continue
    reactions = [x.id for x in list(gene.reactions)]
    for rxn in reactions:
        corda_rxn_confidences[rxn] = confidence
        
for rxn in iJO1366.reactions:
    if rxn.id not in corda_rxn_confidences.keys():
        corda_rxn_confidences[rxn.id] = 0

# Run CORDA       
optimal = CORDA(iJO1366, corda_rxn_confidences)
optimal.build()
CORDA = []
for rxn in optimal.included.keys():
    if optimal.included[rxn] == True:
        CORDA.append(rxn)

### Comparing with and without GPR rules option

In [4]:
# No GPRs
iJO1366_lb_aerobic = riptide.contextualize(iJO1366, transcriptome=lb_aerobic)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 455 from 2583 (82.38% change)
Metabolites pruned to 456 from 1805 (74.74% change)
Flux through the objective DECREASED to ~86.58 from ~105.77 (18.14% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 1 minutes and 21 seconds



In [5]:
# Integrating GPRs
iJO1366_lb_aerobic_gpr = riptide.contextualize(iJO1366, transcriptome=lb_aerobic, gpr=True)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 449 from 2583 (82.62% change)
Metabolites pruned to 452 from 1805 (74.96% change)
Flux through the objective DECREASED to ~87.02 from ~105.77 (17.73% change)
Context-specific metabolism correlates with transcriptome (p<<0.001 ***)

RIPTiDe completed in 1 minutes and 20 seconds



In [8]:
# Compare groups
no_gpr_rxns = set([x.id for x in iJO1366_lb_aerobic.model.reactions])
gpr_rxns = set([y.id for y in iJO1366_lb_aerobic_gpr.model.reactions])

no_gpr_only = no_gpr_rxns.difference(gpr_rxns)
gpr_only = gpr_rxns.difference(no_gpr_rxns)

core_rxns = no_gpr_rxns.intersection(gpr_rxns)

print('Both: ' + str(len(core_rxns)))
print('with GPR:: ' + str(len(gpr_only)))
print('without GPR:: ' + str(len(no_gpr_only)))

Both: 415
with GPR:: 34
without GPR:: 40


### RIPTiDe with Rat Heart Model

In [46]:
# Read in model
from riptide import *
iRno = cobra.io.read_sbml_model('/home/mjenior/Desktop/repos/Jenior_RIPTiDe_2019/data/reconstructions/iRno.xml')

Model does not contain SBML fbc package information.
'' is not a valid SBML 'SId'.
SBML package 'layout' not supported by cobrapy, information is not parsed
SBML package 'render' not supported by cobrapy, information is not parsed
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01285_c "ADP">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01334_c "AMP">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01371_c "ATP">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01252_c "acetate">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01597_c "CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01261_c "acetyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <

Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00003_c "(10Z)-heptadecenoic acid">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00004_c "(10Z)-heptadecenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01237_c "9-heptadecenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01238_c "9-heptadecylenic acid">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00019_c "(13Z)-octadecenoic acid">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00020_c "(13Z)-octadecenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01586_c "cis-vaccenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Sp

Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01756_c "dUTP">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01754_c "dUDP">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01596_m "CO2">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02040_m "H2O">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02046_m "HCO3-">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02039_m "H+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00184_c "[ACP]">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02774_c "propanoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Spe

Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01949_c "GDP-4-dehydro-6-deoxy-D-mannose">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02553_c "NADH">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02039_c "H+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01950_c "GDP-L-fucose">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02552_c "NAD+">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m02771_c "propane-1,2-diol">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m01715_c "D-lactaldehyde">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00648_c "2-hydroxybutyrate">
Use of FORMULA in the notes 

Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00125_c "(8Z,11Z,14Z,17Z)-eicosatetraenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00464_c "1-acylglycerol-3P-8,11,14,17-eico">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00103_c "(5Z,8Z,11Z,14Z,17Z)-eicosapentaenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00452_c "1-acylglycerol-3P-5,8,11,14,17-eico">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00121_c "(7Z,10Z,13Z,16Z,19Z)-docosapentaenoyl-CoA">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00459_c "1-acylglycerol-3P-7,10,13,16,19-docosa">
Use of FORMULA in the notes element is discouraged, use fbc:chemicalFormula instead: <Species M_m00466_c "1-acylglycerol-3

...

Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41537 "chloride / Na+ / NH4+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41538 "chloride / NH4+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41539 "chloride / formate antiport [cs~cs]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41540 "retinol uniport [s-c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41541 "dopamine uniport [c-s]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41542 "dopamine / 2x Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41543 "iodide / Na

Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41594 "Na+ / pantothenate active transport  [s>c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41595 "proline / 2x Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41596 "palmitate Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41597 "oleate / Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41598 "stearate / Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41599 "eicosanoate / Na+ symport [s=c]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR41600 "

Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90028 "inositol-1,3,4,5,6-pentakisphosphate 3-phosphatase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90029 "inositol-1,4,5,6-tetrakisphosphate 6-phosphatase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90030 "inositol-4,5-bisphosphate 5-phosphatase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90033 "selenate reductase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90036 "glutamate: coenzyme F420-0 ligase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90037 "glutamate: coenzyme F420-2 ligase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObje

Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90094 "taurodehydrocholic acid exchange">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90095 "alpha-muricholyol-CoA hydrolase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90096 "alpha-muricholoyl-CoA: taurine-transferase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90097 "beta-muricholate:CoA ligase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90098 "beta-muricholoyl-CoA hydrolase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90099 "beta-muricholoyl-CoA: taurine-transferase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Re

Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90163 "hyodeoxycholate:CoA ligase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90164 "hyodeoxycholoyl-CoA hydrolase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90165 "hyodeoxycholoyl-CoA: taurine-transferase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90166 "hyodeoxycholoyl-CoA: glycine-transferase">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90167 "hyodeoxycholate active transport  [c>s]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxObjective instead: <Reaction R_RCR90168 "tauro-hyodeoxycholic acid active transport  [c>s]">
Encoding OBJECTIVE_COEFFICIENT in KineticLaw is discouraged, use fbc:fluxOb

In [48]:
iRno

<Model  at 0x7fd2e960c590>

In [49]:
iRno.slim_optimize()

0.05095693372190105

In [18]:
# Constrain media condition - 
exchanges = ['RCR30315','RCR90123','RCR30024','RCR30046','RCR30045','RCR30032','RCR30013','RCR30015','RCR30014','RCR30145','RCR30095','RCR30005','RCR30321','RCR30116','RCR30527','RCR30528','RCR30529','RCR30530','RCR30531','RCR90202','RCR30184','RCR30117','RCR30042','RCR30317','RCR30318','RCR30031','RCR30185']

for rxn in iCardio.reactions:
    if len(rxn.products) == 0:
        if not rxn.id in exchanges:
            rxn.bounds = (0., min([rxn.upper_bound, 1000.]))
        else:
            rxn.bounds = (max([rxn.lower_bound, -1000.]), min([rxn.upper_bound, 1000.]))

In [19]:
print('Genes: ' + str(len(iCardio.genes)))
print('Objective value: ' + str(iCardio.slim_optimize()))

Genes: 1728
Objective value: 761.7658939393942


In [50]:
# Read in Doxycycline 24 hour transcriptomic data and run RIPTiDe
dox_24 = riptide.read_transcription_file(file='/home/mjenior/Desktop/iCardio/Dox_24.tsv', 
                                         header=True, replicates=True)

# Read in DMSO 24 hour transcriptomic data and run RIPTiDe (second replicate)
dmso_24 = riptide.read_transcription_file(file='/home/mjenior/Desktop/iCardio/DMSO2_24.tsv', 
                                            header=True, replicates=True)

In [51]:
# RIPTiDe with default parameters
iRno_dox_24 = riptide.contextualize(iRno, transcriptome=dox_24)


Initializing model and integrating transcriptomic data...


KeyboardInterrupt: 

Process ForkPoolWorker-127:
Traceback (most recent call last):
  File "/home/mjenior/anaconda3/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/mjenior/anaconda3/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/mjenior/anaconda3/lib/python3.7/multiprocessing/pool.py", line 121, in worker
    result = (True, func(*args, **kwds))
  File "/home/mjenior/anaconda3/lib/python3.7/multiprocessing/pool.py", line 44, in mapstar
    return list(map(*args))
  File "/home/mjenior/.local/lib/python3.7/site-packages/cobra/flux_analysis/variability.py", line 47, in _fva_step
    _model.slim_optimize()
  File "/home/mjenior/.local/lib/python3.7/site-packages/cobra/core/model.py", line 1049, in slim_optimize
    self.solver.optimize()
  File "/home/mjenior/.local/lib/python3.7/site-packages/optlang/interface.py", line 1471, in optimize
    status = self._optimize()
  File "/home/mjenior/.

In [24]:
# RIPTiDe with default parameters
iCardio_dmso_24 = riptide.contextualize(iCardio, transcriptome=dmso_24)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 112 from 4183 (97.32% change)
Metabolites pruned to 126 from 2886 (95.63% change)
Flux through the objective DECREASED to ~630.76 from ~761.77 (17.2% change)
Context-specific metabolism correlates with transcriptome (p=0.008 **)

RIPTiDe completed in 3 minutes and 25 seconds



In [25]:
# Compare resultant model topology

test1 = set([x.id for x in iCardio_dox_24.model.genes])
test2 = set([x.id for x in iCardio_dmso_24.model.genes])

dox_only_gene = list(test1.difference(test2))
dmso_only_gene = list(test2.difference(test1))
core_gene = list(test1.intersection(test2))

print('Dox 24 hr only genes: ' + str(len(dox_only_gene)))
print('DMSO 24 hr only genes: ' + str(len(dmso_only_gene)) + '\n')

#--------------------------------------------------------------------------#

test1 = set([x.id for x in iCardio_dox_24.model.reactions])
test2 = set([x.id for x in iCardio_dmso_24.model.reactions])

dox_only_rxn = list(test1.difference(test2))
dmso_only_rxn = list(test2.difference(test1))
core_rxn = list(test1.intersection(test2))

print('Dox 24 hr only reactions: ' + str(len(dox_only_rxn)))
print('DMSO 24 hr only reactions: ' + str(len(dmso_only_rxn)) + '\n')

#--------------------------------------------------------------------------#

test1 = set([x.id for x in iCardio_dox_24.model.metabolites])
test2 = set([x.id for x in iCardio_dmso_24.model.metabolites])

dox_only_cpd = list(test1.difference(test2))
dmso_only_cpd = list(test2.difference(test1))
core_cpd = list(test1.intersection(test2))

print('Dox 24 hr only metabolites: ' + str(len(dox_only_cpd)))
print('DMSO 24 hr only metabolites: ' + str(len(dmso_only_cpd)) + '\n')

#--------------------------------------------------------------------------#

print('Shared genes: ' + str(len(core_gene)))
print('Shared reactions: ' + str(len(core_rxn)))
print('Shared metabolites: ' + str(len(core_cpd)))

Dox 24 hr only genes: 1
DMSO 24 hr only genes: 4

Dox 24 hr only reactions: 3
DMSO 24 hr only reactions: 3

Dox 24 hr only metabolites: 1
DMSO 24 hr only metabolites: 1

Shared genes: 255
Shared reactions: 109
Shared metabolites: 125


In [27]:
# Identify context-specific metabolites
compartments = {'c': 'cytoplasm', 
                'r': 'endoplasmic reticulum', 
                's': 'extracellular space', 
                'm': 'mitochondria', 
                'p': 'peroxisome', 
                'g': 'golgi', 
                'l': 'lysosome', 
                'n': 'nucleus'}


print('Dox 24 hr only metabolites:')
for x in dox_only_cpd:
    name = iCardio_dox_24.model.metabolites.get_by_id(x).name
    compartment = compartments[iCardio_dox_24.model.metabolites.get_by_id(x).compartment]
    print('\t' + name + ' from the ' + compartment)
    
print('\nDMSO 24 hr only metabolites:')
for y in dmso_only_cpd:
    name = iCardio_dmso_24.model.metabolites.get_by_id(y).name
    compartment = compartments[iCardio_dmso_24.model.metabolites.get_by_id(y).compartment]
    print('\t' + name + ' from the ' + compartment)

Dox 24 hr only metabolites:
	2-oxobutyrate from the mitochondria

DMSO 24 hr only metabolites:
	glucosamine-6-phosphate from the cytoplasm


### Runtime comparison

In [1]:
from riptide import *

In [2]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/e_coli_core.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 57 from 95 (40.0% change)
Metabolites pruned to 58 from 72 (19.44% change)
Flux through the objective DECREASED to ~39.63 from ~40.85 (2.99% change)

RIPTiDe completed in 7 seconds



In [3]:
test_model

<Model e_coli_core at 0x7f9faa3c6190>

In [4]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iIT341.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 317 from 554 (42.78% change)
Metabolites pruned to 316 from 485 (34.85% change)
Flux through the objective DECREASED to ~113.9 from ~165.41 (31.14% change)

RIPTiDe completed in 36 seconds



In [5]:
test_model

<Model iIT341 at 0x7f9fc5bc2110>

In [27]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iIS312.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 140 from 519 (73.03% change)
Metabolites pruned to 149 from 606 (75.41% change)
Flux through the objective DECREASED to ~49.98 from ~50.68 (1.38% change)

RIPTiDe completed in 11 seconds



In [7]:
test_model

<Model iIS312 at 0x7f9fc5f6a950>

In [25]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iNF517.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 51 from 754 (93.24% change)
Metabolites pruned to 67 from 650 (89.69% change)
Flux through the objective DECREASED to ~79.78 from ~91.53 (12.84% change)

RIPTiDe completed in 12 seconds



In [26]:
test_model

<Model iNF517 at 0x7f9f8b2e78d0>

In [10]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iAM_Pf480.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 439 from 1083 (59.46% change)
Metabolites pruned to 446 from 909 (50.94% change)
Flux through the objective DECREASED to ~279.34 from ~329.17 (15.14% change)

RIPTiDe completed in 25 seconds



In [11]:
test_model

<Model iAM_Pf480 at 0x7f9fa89d90d0>

In [12]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iEK1008.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 447 from 1226 (63.54% change)
Metabolites pruned to 451 from 998 (54.81% change)
Flux through the objective DECREASED to ~41.01 from ~45.45 (9.77% change)

RIPTiDe completed in 37 seconds



In [13]:
test_model

<Model iEK1008 at 0x7f9f9bcdcc10>

In [14]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iJO1366.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 371 from 2583 (85.64% change)
Metabolites pruned to 374 from 1805 (79.28% change)
Flux through the objective DECREASED to ~86.73 from ~105.66 (17.92% change)

RIPTiDe completed in 33 seconds



In [15]:
test_model

<Model iJO1366 at 0x7f9f9b2e54d0>

In [16]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iSFxv_1172.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 363 from 2638 (86.24% change)
Metabolites pruned to 367 from 1918 (80.87% change)
Flux through the objective DECREASED to ~65.3 from ~88.16 (25.93% change)

RIPTiDe completed in 31 seconds



In [17]:
test_model

<Model iSFxv_1172 at 0x7f9f9a450910>

In [18]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iMM1415.xml')
test_model.objective = test_model.reactions.BIOMASS_mm_1_no_glygln
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)

No objective coefficients in model. Unclear what should be optimized



Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 253 from 3726 (93.21% change)
Metabolites pruned to 254 from 2775 (90.85% change)
Flux through the objective DECREASED to ~464.48 from ~567.04 (18.09% change)

RIPTiDe completed in 48 seconds



In [19]:
test_model

<Model iMM1415 at 0x7f9f991d1690>

In [21]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/iCHOv1.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 242 from 6663 (96.37% change)
Metabolites pruned to 243 from 4456 (94.55% change)
Flux through the objective DECREASED to ~274.39 from ~341.64 (19.68% change)

RIPTiDe completed in 1 minutes and 28 seconds



In [22]:
test_model

<Model iCHOv1 at 0x7f9fa850b050>

In [23]:
# Read in model
test_model = cobra.io.read_sbml_model('/home/mjenior/Desktop/reconstructions/Recon3D.xml')
# Open all exchanges
for rxn in test_model.reactions:
    if len(rxn.reactants) == 0 or len(rxn.products) == 0:
        rxn.bounds = (-1000., 1000.)
# Create simulated transcriptome
test_transcriptome = {}
for gene in test_model.genes:
    test_transcriptome[gene.id] = 1.0
# Run RIPTiDe
test = riptide.contextualize(test_model, transcriptome=test_transcriptome)


Initializing model and integrating transcriptomic data...
Pruning zero flux subnetworks...
Analyzing context-specific flux distributions...

Reactions pruned to 280 from 10600 (97.36% change)
Metabolites pruned to 266 from 5835 (95.44% change)
Flux through the objective DECREASED to ~662.44 from ~823.21 (19.53% change)

RIPTiDe completed in 4 minutes and 30 seconds



In [24]:
test_model

<Model Recon3D at 0x7f9f94c82d10>